# Import data

You can import data from either:

## ...from CSV

The import code in this section is specific to the CSV automatically generated for each collective dialouge on remesh.


Get the CSV from Remesh: **Export Data > Conversation Data > Download CSV > Sorted by Question**

In [22]:
# Set this to 'True' to Enable importing from CSV. Set to 'False' to disable.
USE_CSV = True

if USE_CSV:
  # use this to import data from .csv
  from google.colab import files
  import pandas as pd
  import csv
  import io
  import warnings
  warnings.filterwarnings('ignore')

  # set PADDING_ROWS to be the number of non-content rows before the initial column headers in the csv
  PADDING_ROWS = 9
  pd.set_option('display.max_colwidth', 0)
  uploaded = files.upload()
  filename = next(iter(uploaded))
  with open(filename,'r') as file:
    csvreader = csv.reader(file)
    r = 1
    data = []
    qdata = []
    for row in csvreader:
      if r>PADDING_ROWS:
        if len(row) == 0 or not row[0].strip():
          data.append(qdata)
          qdata = []
        else:
          qdata.append(row)
      r=r+1
    data.append(qdata)

  #handle blank row
  data = data[1:]

  #percent string to float
  def p2f(x):
    try:
      if x==' - ':
        return float("nan")
      else:
        return float(x.strip('%'))/100
    except:
      return x

  #make numeric
  nq = len(data)
  qs = []
  meta = [["question type","question text"]]
  for i in range(0,nq):
    d = data[i]
    m = [d[1][1],d[1][2]]
    meta.append(m)
    if d[1][1] == 'Poll Single Select':
      for r in range(1,len(d)):
        for c in range(4,len(d[0])):
          d[r][c] = p2f(d[r][c])
    if d[1][1] == 'Ask Opinion':
      for r in range(1,len(d)):
        for c in range(6,len(d[0])-3):
          d[r][c] = p2f(d[r][c])
    df = pd.DataFrame(d[1:],columns = d[0])
    qs.append(df)
  qmeta = pd.DataFrame(meta[1:],columns = meta[0])

Saving GD3_march_2025_aggregate - GD3_march_2025_aggregate.csv to GD3_march_2025_aggregate - GD3_march_2025_aggregate.csv


## ...from json

This imports the aggregated data set from a json file, usually which has response text embeddings appended for doing retrieval stuff.

In [5]:
# Set this to 'True' to Enable importing from JSON. Set to 'False' to disable.
USE_JSON = False
import json
import pandas as pd
import requests

if USE_JSON:
  # use this to import data from .json
  from google.colab import files
  import io
  import warnings
  warnings.filterwarnings('ignore')

  GD1_DOWNLOAD = 'https://drive.usercontent.google.com/download?id=14JfhnqQiDpvMTGH-mJc04Fg4UubED9_7&export=download&authuser=0&confirm=t&uuid=ea5e840c-7ecc-4dd8-a4e3-d8810f13a54e&at=AEz70l4pHJVk7x335P-7ag8ccrdf%3A1742574770488'

  # Use this to download the JSON with text embeddings computed from GDrive
  # OR set to False to upload the JSON file from your own computer
  USE_DIRECT_DOWNLOAD = True



  if USE_DIRECT_DOWNLOAD:
      download_url = GD1_DOWNLOAD
      response = requests.get(download_url)

      if response.status_code != 200:
          raise Exception(f"Failed to download file: Status code {response.status_code}")

      loaded_list = json.loads(response.text)

  else:
    uploaded = files.upload()
    filename = next(iter(uploaded))
    with open(filename,'r') as file:
        loaded_list = json.load(file)

  # Convert the list of dictionaries back to DataFrames
  qs = [pd.DataFrame(df) for df in loaded_list]

## ...from saved progress
Save progress in this notebook at any time with these functions.

Save automatically to Google Drive.

Efficiently reload state from a saved .pkl file.

In [1]:
# Set this to 'True' to automatically load the last-saved .pkl datafile when running this notebook.
# When working iteratively in the notebook and saving updates to the qs data structure,
# this is the fastest way to save & reload state in the notebook.
USE_AUTOLOAD_PROGRESS = True

import pickle
import os
import datetime
from google.colab import files
import io

DEFAULT_GDRIVE_PATH = '/content/drive/MyDrive/saved_colab_data/GD3'

def save_data_to_download(data, filename=None):
    """
    Save the data structure to a pickle file and download it to the user's local machine.

    Args:
        data: The data structure to save
        filename: Optional custom filename (default: auto-generated with timestamp)

    Returns:
        None
    """
    # Generate filename with timestamp if not provided
    if filename is None:
        timestamp = datetime.datetime.now().strftime("%Y%m%d_%H%M%S")
        filename = f"qs_data_{timestamp}.pkl"

    # Ensure filename has .pkl extension
    if not filename.endswith('.pkl'):
        filename += '.pkl'

    # Save data using pickle to a temporary file
    with open(filename, 'wb') as f:
        pickle.dump(data, f, protocol=pickle.HIGHEST_PROTOCOL)

    # Download the file to user's local machine
    files.download(filename)
    print(f"File '{filename}' has been prepared for download. Check your browser's download area.")


def upload_and_load_data():
    """
    Upload a pickle file from the user's local machine and load the data structure.

    Returns:
        The loaded data structure
    """
    print("Please select your saved pickle file (.pkl) to upload...")
    uploaded = files.upload()

    if not uploaded:
        print("No file was uploaded.")
        return None

    # Get the filename of the uploaded file
    filename = list(uploaded.keys())[0]

    if not filename.endswith('.pkl'):
        print(f"Warning: The uploaded file '{filename}' does not have a .pkl extension.")

    # Load data using pickle
    try:
        with open(filename, 'rb') as f:
            data = pickle.load(f)

        print(f"Data successfully loaded from '{filename}'")
        return data
    except Exception as e:
        print(f"Error loading data: {e}")
        return None


def save_data_to_drive(data, filename=None, drive_path=None):
    """
    Save the data structure to a pickle file in Google Drive.

    Args:
        data: The data structure to save
        filename: Optional custom filename (default: auto-generated with timestamp)
        drive_path: Path in Google Drive to save the file (default: root)

    Returns:
        Path to the saved file
    """
    # Make sure Google Drive is mounted
    try:
        from google.colab import drive
        drive_mounted = True
    except:
        print("Warning: Google Drive module not available.")
        return None

    # Mount Google Drive if not already mounted
    import os
    if not os.path.exists('/content/drive'):
        drive.mount('/content/drive')
        print("Google Drive mounted.")

    # Generate filename with timestamp if not provided
    if filename is None:
        timestamp = datetime.datetime.now().strftime("%Y%m%d_%H%M%S")
        filename = f"qs_data_{timestamp}.pkl"

    # Ensure filename has .pkl extension
    if not filename.endswith('.pkl'):
        filename += '.pkl'

    # Set the default drive path
    if drive_path is None:
        drive_path = DEFAULT_GDRIVE_PATH

    # Create directory if it doesn't exist
    if not os.path.exists(drive_path):
        os.makedirs(drive_path)

    # Full path to save file
    filepath = os.path.join(drive_path, filename)

    # Save data using pickle
    try:
        with open(filepath, 'wb') as f:
            pickle.dump(data, f, protocol=pickle.HIGHEST_PROTOCOL)

        print(f"Data saved to Google Drive at {filepath}")
        return filepath
    except Exception as e:
        print(f"Error saving data to Google Drive: {e}")
        return None


def load_data_from_drive(filepath=None, drive_path=None):
    """
    Load a data structure from a pickle file in Google Drive.

    Args:
        filepath: Path to the pickle file (if you know the exact path)
        drive_path: Directory in Google Drive to list available files (default: root)

    Returns:
        The loaded data structure, or None if loading failed
    """
    # Make sure Google Drive is mounted
    try:
        from google.colab import drive
        drive_mounted = True
    except:
        print("Error: Google Drive module not available.")
        return None

    # Mount Google Drive if not already mounted
    import os
    if not os.path.exists('/content/drive'):
        drive.mount('/content/drive')
        print("Google Drive mounted.")

    # Set the default drive path
    if drive_path is None and filepath is None:
        drive_path = DEFAULT_GDRIVE_PATH

    # If no specific file is provided, list available files and let user choose
    if filepath is None:
        if not os.path.exists(drive_path):
            print(f"Directory {drive_path} does not exist in Google Drive.")
            return None

        # Get all .pkl files in the directory
        files_list = [f for f in os.listdir(drive_path) if f.endswith('.pkl')]

        if not files_list:
            print(f"No .pkl files found in {drive_path}")
            return None

        # Sort by modification time (newest first)
        files_list.sort(key=lambda x: os.path.getmtime(os.path.join(drive_path, x)), reverse=True)

        # Display available files
        print(f"Available saved data files in {drive_path}:")
        for i, file in enumerate(files_list):
            timestamp = datetime.datetime.fromtimestamp(
                os.path.getmtime(os.path.join(drive_path, file))
            ).strftime("%Y-%m-%d %H:%M:%S")
            print(f"{i+1}. {file} (saved on {timestamp})")

        # Ask user to choose a file
        try:
            choice = input(f"Enter the number of the file to load (1-{len(files_list)}) or press Enter for most recent: ").strip()

            if not choice:  # If no input provided, auto-select first file
                choice = "1"

            choice = int(choice)
            if 1 <= choice <= len(files_list):
                filepath = os.path.join(drive_path, files_list[choice-1])
            else:
                print("Invalid choice.")
                return None
        except ValueError:
            print("Invalid input. Please enter a number or press Enter for most recent.")
            return None

    # Load data using pickle
    try:
        with open(filepath, 'rb') as f:
            data = pickle.load(f)

        print(f"Data loaded from {filepath}")
        return data
    except Exception as e:
        print(f"Error loading data: {e}")
        return None


# Example usage:
"""
# Save data for download to local machine
save_data_to_download(qs) # download as qs_data_YYYYMMDD_HHMMSS.pkl
# OR save_data_to_download(qs, filename="my_analysis_progress.pkl")

# Save data to Google Drive
save_data_to_drive(qs) # saves as qs_data_YYYYMMDD_HHMMSS.pkl at DEFAULT_GDRIVE_PATH
# OR save_data_to_drive(qs, filename="my_analysis_progress.pkl")

# Upload data from local machine (will prompt for file upload)
qs = upload_and_load_data()


# Load data from Google Drive
# (will list available files if filepath not provided and prompt for selection)
qs = load_data_from_drive()

# Or load with explicit path from Google Drive
qs = load_data_from_drive(filepath="/content/drive/MyDrive/my_project/my_analysis_progress.pkl")
"""

if USE_AUTOLOAD_PROGRESS:
  qs = load_data_from_drive()

Mounted at /content/drive
Google Drive mounted.
Available saved data files in /content/drive/MyDrive/saved_colab_data/GD3:
1. qs_data_20250417_201629.pkl (saved on 2025-04-17 20:16:31)
Enter the number of the file to load (1-1) or press Enter for most recent: 
Data loaded from /content/drive/MyDrive/saved_colab_data/GD3/qs_data_20250417_201629.pkl


# Analysis library

### Non-LLM functions

In [2]:
import math
import json
import pandas as pd
pd.set_option('display.max_colwidth', 0)
import matplotlib.pyplot as plt
plt.close("all")

# ----------------------------------
# function to show the questions by ID
def show_questions(qs_):
  questions = meta = [["question type","question text"]]
  for i in range(0,len(qs_)):
    # questions.append([qs_[i]["Question Type"][1],qs_[i]["Question"][1]]) # Previous Andrew code
    # New code: Accessing the first row (index 0) instead of the second (index 1)
    # Also using .iloc to ensure we are accessing the row by position, not by label
    questions.append([qs_[i]["Question Type"].iloc[0],qs_[i]["Question"].iloc[0]])
  return pd.DataFrame(questions[1:],columns = questions[0])

# usage example
#show_questions(qs)
# ----------------------------------


# ----------------------------------
# function to show the segments by ID
def show_segments(qs_):
  segments = []
  q0 = qs_[0]
  if q0["Question Type"][1] == 'Poll Single Select':
    for c in range(4,len(q0.columns)):
      segments.append(q0.columns[c])
  if q0["Question Type"][1] == 'Ask Opinion':
    for c in range(5,len(q0.columns)-3):
      segments.append(q0.columns[c])
  return pd.DataFrame(segments)

# usage example
#show_segments(qs)
# ----------------------------------


# ----------------------------------
# function to plot poll data by segment
def plot_poll(df,segs):
  print(df["Question"][1])
  segs_incl = ['Responses']
  for i in range(0,len(segs)):
    segs_incl.append(df.columns[4+segs[i]])
  dfplt = df[segs_incl]
  dfplt = dfplt.set_index('Responses')
  dfplt.plot.barh()
  return dfplt
# usage example
#qid = 5
#segs = [231,232,233,234,235,236]
#d =plot_poll(qs[qid],segs)
# ----------------------------------


# ----------------------------------
# function to make a results table dataframe look prettier
def make_pretty(styler):
  styler.background_gradient(axis=None, vmin=0, vmax=1, cmap="RdYlGn")
  styler.format(precision=2)
  return styler
# ----------------------------------

# ----------------------------------
# function to generate generate a results table for an opinion ask for a given set of segments
# only works for "Ask Opinion" question types
# df: data set for specific question; usually specificed as qs[qid]
# segs: list of ids corresponding to the segments to include in the table
# n: number of participant responses to include in the table
def table_ask(df,segs,n):
  segs_incl = ['English Responses']
  for i in range(0,len(segs)):
    segs_incl.append(df.columns[7+segs[i]])
  dfplt = df[segs_incl]
  #dfplt = dfplt.set_index('Responses')
  return dfplt.iloc[:n].style.pipe(make_pretty)

# usage example
#qid = 18
#segs = [0,231,232,233,234,235,236]
#print(qs[qid]["Question"][1]) #print the text of the question
#table_ask(qs[qid],segs,10)
# ----------------------------------


# ----------------------------------
# compute max-min bridging metric, used in bridging_ask function
def min_bridge(row,segs_incl,col):
  b = 1
  for s in range(0,len(segs_incl)):
    b_ = row[segs_incl[s]]
    try:
      b_ = float(b_) # Try converting b_ to float
    except ValueError:
      b_ = float('nan') # If conversion fails, set to NaN
    b = min(b,b_)
  return b
# ----------------------------------


# ----------------------------------
# compute max-min polarization metric, used in bridging_ask function
def polarization(row,segs_incl,col):
  mx = 0
  mn = 1
  for s in range(0,len(segs_incl)):
    b_ = row[segs_incl[s]]
    try:
      b_ = float(b_)  # Try converting to float
    except ValueError:
      b_ = float('nan')  # Handle non-numeric values by setting to NaN
    mx = max(mx,b_)
    mn = min(mn,b_)
  return mx-mn
# ----------------------------------


# ----------------------------------
# compute max-min divergence metric, used in bridging_ask function
def symmetric_divergence(row,segs_incl,col):
  mx = 0
  mn = 1
  for s in range(0,len(segs_incl)):
    b_ = row[segs_incl[s]]
    try:
      b_ = float(b_)  # Try converting to float
    except ValueError:
      b_ = float('nan')  # Handle non-numeric values by setting to NaN
    mx = max(mx,b_)
    mn = min(mn,b_)
  mx_div = max(mx-0.5,0)
  mn_div = max(0.5-mn,0)
  return math.sqrt(mx_div*mn_div)
# ----------------------------------


# ----------------------------------
# generate dataframe which includes bridging, polarization, divergence metrics
# only works for "Ask Opinion" question types
def bridging_ask(df,segs):
  segs_incl = ['English Responses']
  for i in range(0,len(segs)):
    segs_incl.append(df.columns[7+segs[i]])
  dfplt = df[segs_incl]
  dfplt["bridge"] = df.apply (lambda row: min_bridge(row,segs_incl[1:],df.columns), axis=1)
  dfplt["polarization"] = df.apply (lambda row: polarization(row,segs_incl[1:],df.columns), axis=1)
  dfplt["divergence"] = df.apply (lambda row: symmetric_divergence(row,segs_incl[1:],df.columns), axis=1)
  return dfplt.sort_values(by=["bridge"],ascending=False)

# usage example
#qid = 15
#segs = [0,231,232,233,234,235]
#print(qs[qid]["Question"][1]) #print the question text
#ba = bridging_ask(qs[qid],segs).iloc[:10] #generate a table of the first 10 responses with the different max-min metrics
#ba.style.pipe(make_pretty) #display the table and make it pretty
# ----------------------------------


# ----------------------------------
#function to get responses whose bridging agreement across a given set of segments is over a specified threshold
def get_bridging_responses(df,segs,thresh):
  bdf = bridging_ask(df,segs)
  return bdf.loc[bdf['bridge']>thresh]

# usage example
#qid = 12
#segs = [0,231,232,233,234,235,236]
#thresh = .50
#print(qs[qid]["Question"][1]) #print question text
#ba = get_bridging_responses(qs[qid],segs,thresh) #get bridging responses
#ba.style.pipe(make_pretty) #display in a pretty table
# ----------------------------------


# ----------------------------------
#function to get the top n responses with highest polarization across a set of segments
def get_polarizing_responses(df,segs,n):
  bdf = bridging_ask(df,segs)
  bdfp = bdf.sort_values(by=["polarization"],ascending=False)
  return bdfp.iloc[:n]
# ----------------------------------


# ----------------------------------
#function to get the top n responses with most divergent responses across a set of segments
def get_divergent_responses(df,segs,n):
  bdf = bridging_ask(df,segs)
  bdfp = bdf.sort_values(by=["divergence"],ascending=False)
  return bdfp.iloc[:n]
# ----------------------------------


# ----------------------------------
#generate a text summary of the n responses with the highest polarization
def polarization_summary(df,segs,n):
  pa = get_polarizing_responses(df,segs,n)

  # Exclude first column and last two columns for min/max calculations
  temp_pa = pa.iloc[:, 1:-2]

  # Find the column names of min and max values
  min_col = temp_pa.idxmin(axis=1)
  max_col = temp_pa.idxmax(axis=1)

  # Find the min and max values
  min_val = temp_pa.min(axis=1)
  max_val = temp_pa.max(axis=1)

  for idx in pa.index:
      first_col_text = pa.loc[idx, pa.columns[0]]
      min_col_name = min_col.loc[idx]
      max_col_name = max_col.loc[idx]
      min_value = pa.loc[idx, min_col_name]
      max_value = pa.loc[idx, max_col_name]
      print(first_col_text)
      print("Low : " + str(int(min_value*100)) +"% -- " + min_col_name )
      print("High : " + str(int(max_value*100)) +"% -- " + max_col_name )
      print(" ")

# usage example
#qid = 16
#segs = [0,231,232,233,234,235]
#n = 10
#print(qs[qid]["Question"][1])
#polarization_summary(qs[qid],segs,n)
# ----------------------------------


# ----------------------------------
#generate a text summary of the n responses with the highest (symetric) divergence
def divergence_summary(df,segs,n):
  pa = get_divergent_responses(df,segs,n)

  # Exclude first column and last two columns for min/max calculations
  temp_pa = pa.iloc[:, 1:-2]

  # Find the column names of min and max values
  min_col = temp_pa.idxmin(axis=1)
  max_col = temp_pa.idxmax(axis=1)

  # Find the min and max values
  min_val = temp_pa.min(axis=1)
  max_val = temp_pa.max(axis=1)

  for idx in pa.index:
      first_col_text = pa.loc[idx, pa.columns[0]]
      min_col_name = min_col.loc[idx]
      max_col_name = max_col.loc[idx]
      min_value = pa.loc[idx, min_col_name]
      max_value = pa.loc[idx, max_col_name]
      print(first_col_text)
      print("Low : " + str(int(min_value*100)) +"% -- " + min_col_name )
      print("High : " + str(int(max_value*100)) +"% -- " + max_col_name )
      print(" ")

# usage example
#qid = 16
#segs = [0,231,232,233,234,235]
#n = 10
#print(qs[qid]["Question"][1])
#divergence_summary(qs[qid],segs,n)
#polarization_summary(qs[qid],segs,n)
# ----------------------------------


# ----------------------------------
# function to save qs as a json object that can be reloaded via json import above
# current use is to save a version of qs with embeddings
# can be used to save a qs with other custom stuff done to it tho
def save_qs_to_json(qs,filename):
  qx = []
  for i in range(0,len(qs)):
    qx.append(qs[i].to_dict())

  # Save the list of dictionaries to a JSON file
  with open(filename, 'w') as f:
      json.dump(qx, f)
# example usage
#save_qs_to_json(qs,"global_inputs_v2.json")
# ----------------------------------

### LLM-based functions


In [8]:
# install stuff and set api key (takes about 1 min to run)
!pip install langchain
!pip install openai
!pip install -U sentence-transformers
!pip install -U langchain-openai
import os

# use this import if running notebook in Google Colab to get the secret key
from google.colab import userdata

os.environ["OPENAI_API_KEY"] = userdata.get('OPENAI_API_KEY') # OR "your-api-key-here"




   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 345.7/345.7 kB 5.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 1.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 62.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 53.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 28.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 794.3 kB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 6.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 10.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 8.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 6.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 75.5 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitlink-cu12
    Found existing installation: nvidia-nvjitlink-cu12 12.5.82
    Uninstall

In [9]:
from langchain_openai import ChatOpenAI
from langchain.prompts import PromptTemplate
from langchain.chains import LLMChain
from langchain.chains import SequentialChain
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np
import random
from openai import OpenAI
client = OpenAI()

# ----------------------------------
# function to generate generate 1024 dimension embeddinggs using text-embedding-3-small model
def get_embedding(text, model="text-embedding-3-small",dimensions=1024):
   text = text.replace("\n", " ")
   return client.embeddings.create(input = [text], model=model,dimensions=dimensions).data[0].embedding
# ----------------------------------


# ----------------------------------
# function to add embeddings to a row qs data frame
def embed_response(row):
  text = row["English Responses"]
  #print(text)
  return get_embedding(text)
# ----------------------------------


# ----------------------------------
# function to add embeddings for all responses in a qs data frame
# used to enable "relevence" ranking
def embed_responses(df):
  #print("begin")
  df["embedding"] = df.apply (lambda row: embed_response(row), axis=1)
  return df
# ----------------------------------


# ---------------------------------
# function to generate embeddings for all open end resposnes in qs
# does not need to be run if you imported a dataset from json that already has embeddings
# !!**WARNING**!!  takes ~2m per 1000 resposnes to run; ie. 45 min for the global inputs data set
def add_embeddings_for_all_responses(qs):
  if USE_DIRECT_DOWNLOAD:
        raise SystemExit("You already have the JSON with text embeddings!\n"
                        "You do not need to run this embedding generation function.")
  questions = show_questions(qs)
  oe_ids = []
  for i in range(0,len(questions)):
    if "Ask" in questions.iloc[i][0]:
      oe_ids.append(i)
      qs[i] = embed_responses(qs[i])
      print(i)
  return qs
# usage example
#qs = add_embeddings_for_all_responses(qs)
# ----------------------------------


# ----------------------------------
# function to rank responses in a qs data frame by simiarlity to a given text
# if data not loaded via json w embeddings, then qs[i] = embed_responses(qs[i]) must be run before this works
def rank_by_similarity(qs, text):
    new_embedding = get_embedding(text)
    qs_copy = qs.copy()

    # Replace NaN embeddings with zero vectors (assuming all embeddings have the same length)
    embedding_dim = len(new_embedding)  # Assuming all embeddings have the same size as the new embedding
    embeddings = np.array([
        np.zeros(embedding_dim) if isinstance(embedding, float) and np.isnan(embedding) else embedding
        for embedding in qs_copy['embedding'].values
    ])

    similarities = cosine_similarity([new_embedding], embeddings)[0]

    # Add the similarities as a new column in the copied dataframe
    qs_copy['cosine_similarity'] = similarities

    # Sort the copied dataframe by cosine similarity in descending order
    qs_sorted = qs_copy.sort_values(by='cosine_similarity', ascending=False)

    return qs_sorted
# ----------------------------------


# ----------------------------------
# Create the components for the prompt chain that powers the main LLM synthesis function

#load LLM
llm = ChatOpenAI(temperature=0.2,model_name='gpt-4-0125-preview')


#summarization prompt
rerankPrompt = PromptTemplate(
    input_variables=["question","responses","query"],
    template="""
    Participants in a research study were asked '{question}'.

    These are their responses:
    {responses}

    Filter the responses, keeping only the responses that are atleast somewhat related to or helpful in anwsering: {query}
    Rank the filtered resposnes starting with the most related to or helpful in answering: {query}
    Output this set of responses formated exactly in the way they are given above, with a newline spereate each response.
    If there are no related response, output "there are no relevant responses"
    """
)
#add to chain
rerankChain = LLMChain(llm=llm, prompt=rerankPrompt,output_key="reranked_responses")


#summarization prompt
summaryPrompt = PromptTemplate(
    input_variables=["question","responses","focus"],
    template="""
    Participants in a research study were asked '{question}'.

    These are their responses:
    {responses}

    Create a hierarchical taxonomy of the unique ideas and themes within these responses using very short bullet points. Avoid dupliate ideas. If there are no responses to analyze, do not provide a taxonomy. Do not include anything in the taxonomy not included in the responses.
    {focus}
    """
    #Summarize all of the unique ideas within these responses into very short bullet points.
)
#add to chain
summaryChain = LLMChain(llm=llm, prompt=summaryPrompt,output_key="summary")


#summarization prompt
bulletsPrompt = PromptTemplate(
    input_variables=["question","summary","focus"],
    template="""
    Participants in a research study were asked '{question}'.

    The TAXONOMY of ideas in participants responses are:
    {summary}

    Summarize the TAXONOMY into 1-15 concise bullet points, with each bullet point starting with a single theme and then overviewing the ideas within that theme. Be direct and specific, DO NOT say things like "Particpants said" or "responses" or "there was a desire" or "this theme" or "focusing on". Just say the ideas. NEVER repeat a theme or idea. A theme name should not include "and". Each bullet should be very short. Each bullets must ONLY contain ideas from the taxonomy. If there is no taxonomy, just output "no ideas to synthesize"

    {focus}

    Example bullet points:
    - Creaive outlets: music, drawing, painting, writing stories, designing houses, creating new receipes, home remodeling.
    - Health improvement: Increased exercise, better diets, access to high-quality healthcare, and reduction of chronic diseases.
    """
)
#add to chain
bulletsChain = LLMChain(llm=llm, prompt=bulletsPrompt,output_key="bullets")

#outcome prompt
outcomePrompt = PromptTemplate(
    input_variables=["question","summary","responses"],
    template="""
    Participants in a research study were asked '{question}'.

    These are their responses:
    {responses}

    The main ideas from these responses are:
    {summary}

    We define an 'outcome' to be a single specific concrete result that can be observed and measured in the world. An 'outcome' should NOT include an explination of how it is acheived (ie. an 'outcome' should NOT include the words "due to" or "as a result of" or "through" or "by" etc.). An 'outcome' MUST be specific enough to be objectively observed or measured.

    Write a list of the 'outcomes' present in the main ideas from the responses summarized above. DO NOT REPEAT ANY IDEAS.

    Here are some examples of 'outcomes':

    - Earths climate remains below 15C
    - The number of gun deaths decreases to below 100 per day globally
    - The fraction of people who cannot afford or access healthcare decreases
    - No nuclear devices are detonated within 100 miles of a human
    - More people report being happy with their life

    """
)
#add to chain
outcomeChain = LLMChain(llm=llm, prompt=outcomePrompt,output_key="outcomes")


#values prompt
valuePrompt = PromptTemplate(
    input_variables=["question","summary","responses"],
    template="""
    Participants in a research study were asked '{question}'.

    These are their responses:
    {responses}

    The main ideas from these responses are:
    {summary}

    We define an 'value' to be a deontilogical property that can be reflected on how an AI behaves, reguardless of the result of that behavior. We do not consider a specific AI behavior to be a 'value'. For example "non-judegment: the AI's behavior does not imply a value judgement about the users feelings or experience" IS a 'value' , but "the AI does not say 'I am judgeing you'" is NOT a 'value'.

    Write a list of the unique 'values' present in the  main ideas from the responses summarized above.

    Here are some example 'values':

    - Empathy: Showing understanding and compassion to make the user feel heard and supported.
    - Respect: Honoring the user's feelings and experiences without minimizing their pain or struggles.
    - Non-judgment: Providing support without criticism or bias to create a safe space for the user to express themselves.

    DO NOT COPY THE EXAMPLE 'values' ABOVE VERBATIM. Construct them based on the responses and summarized ideas above.

    """
)
#add to chain
valueChain = LLMChain(llm=llm, prompt=valuePrompt,output_key="values")

#generate all the sequential chains
genSummaryChain = SequentialChain(
    chains=[summaryChain],
    input_variables=["question", "responses","focus"],
    output_variables=["summary"],
    verbose=False)

genOutcomeChain = SequentialChain(
    chains=[summaryChain, outcomeChain],
    input_variables=["question", "responses","focus"],
    output_variables=["summary","outcomes"],
    verbose=False)

genValuesChain = SequentialChain(
    chains=[summaryChain, valueChain],
    input_variables=["question", "responses","focus"],
    output_variables=["summary","values"],
    verbose=False)

genBulletsChain = SequentialChain(
    chains=[summaryChain, bulletsChain],
    input_variables=["question", "responses","focus"],
    output_variables=["summary","bullets"],
    verbose=False)

rerankOnlyChain = SequentialChain(
    chains=[rerankChain],
    input_variables=["question", "responses","query"],
    output_variables=["reranked_responses"],
    verbose=False)
# ----------------------------------



# ----------------------------------
# function to run the main LLM synthesis pipeline
# qs: main question data object
# qid: = quesiton id
# segs: list with segment ids to be used in the analysis
# synth_type: type of synthesis to generate, can be set to..
#                          "summary" = taxonomy of unique ideas in selected responses
#                          "bullets" = 10ish bullets based on the taxonomy of unique ideas in selected responses
#                          "outcomes" = a list of specific outcomes derived from the selected responses
#                          "values" = a list of values derived from the selected responses
# rank_type: the way that responses will be ranked and selected for use in synthesis, can be set to...
#                          "bridging" = smallest agreement value within any of the given segments (max-min bridging), ranks by decending,  thresh filters by greater than
#                          "polarization" = difference between the segments with largest and smallest agreement
#                          "divergence" = geometric mean of the deveations from 50% of the agreements from the segments with largest and smallest agreement
#                          "low_agreement" = smallest agreement value within any of the given segments (max-min bridging), ranks by assending, thresh filters by less than
#                          "relevance" = cosine_similarity to query_text, can only be used if responses have embeddings (ie. data loaded from a json with embeddings pre-appended, or after uses [this function] to append embeddings)
#                          "sample" = randomly samples n_max responses
# thresh: the threshold value used to filter and select responses for the given rank_type
# n_max: maximium number of response to include in the set of selected responses
# query_text: used to rank and filter resposnes if rank_type = "relevance", else if *not blank* is used to filter responses and focus synthesis

def synthesize(qs,qid,segs,synth_type,rank_type,thresh,n_max,query_text = ""):

  #build string of responses
  if rank_type == "bridging":
    print("ranking by bridging")
    ba_ = get_bridging_responses(qs[qid],segs,thresh)
    ba = ba_.iloc[:n_max]
  elif rank_type == "polarization":
    print("ranking by polarization")
    ba = get_polarizing_responses(qs[qid],segs,n_max)
  elif rank_type == "divergence":
    print("ranking by divergence")
    ba = get_divergent_responses(qs[qid],segs,n_max)
  elif rank_type == "low_agreement":
    print("ranking by low agreement")
    ba_ = bridging_ask(qs[qid],segs)
    ba_ = ba_.sort_values(by=["bridge"],ascending=True)
    ba_ = ba_.loc[ba_["bridge"]<thresh]
    ba = ba_.iloc[:n_max]
  elif rank_type == "relevance":
    ba_ = rank_by_similarity(qs[qid], query_text)
    ba_ = ba_.loc[ba_["cosine_similarity"]>thresh]
    ba = ba_.iloc[:n_max]
  else:
    print("random sampling")
    ba_ = get_bridging_responses(qs[qid],segs,0)
    ba = ba_.sample(n=n_max)

  responses_str = ''
  for ind in ba.index:
    rsp = ba["English Responses"][ind]
     # Convert rsp to string before concatenation to handle potential floats
    responses_str+="-"
    responses_str+=str(rsp)
    responses_str+="\n \n "

  #get quesiton text
  df = qs[qid]
  question_str = df["Question"].iloc[0]

  #filter responses for relevance if there is a query term
  if query_text != "":
    focus = "only include topics and themes that are reasonably relevant to: " + query_text
    prelim_responses = rerankOnlyChain({
        "question":question_str,
        "responses":responses_str,
        "query":query_text
    })
    responses_str = prelim_responses["reranked_responses"]
  else:
    focus = ""

  #select prompt chain to run based on synth_type
  if synth_type == "outcomes":
    out = genOutcomeChain({
        "question":question_str,
        "responses":responses_str,
        "focus":focus
    })
  if synth_type == "values":
    out = genValuesChain({
        "question":question_str,
        "responses":responses_str,
        "focus":focus
    })
  if synth_type == "bullets":
    out = genBulletsChain({
        "question":question_str,
        "responses":responses_str,
        "focus":focus
    })
  if synth_type == "summary":
    out = genSummaryChain({
        "question":question_str,
        "responses":responses_str,
        "focus":focus
    })
  out["data"]=ba
  return out

# usage example [TODO]
#qid = 10
#segs = [0,231,232,233,234,235]
#synth_type = "bullets"      #synthesize results as bullet points
#rank_type = "bridging"      #ranking responses to synthesize by bridgage agreement across [segs]
#thresh = .50                #only keep responses where 50%+ participants in all [segs] agree
#n_max = 100                 #only keep the top 100 responses withi highest bridging agreement
#query_text = "enviroment"   #focus on resposnes and sythesized results related to "enviroment"

#out = synthesize(qs,qid,segs,synth_type,rank_type,thresh,n_max,query_text = query_text) #run the sytthesis
#print(qs[qid]["Question"][1]) #print quesiton text
#print(out[synth_type]) #print synthesis results
#dat = out["data"] #get the data set used for results sythesis

<ipython-input-9-3348aa8346d1>:108: LangChainDeprecationWarning: The class `LLMChain` was deprecated in LangChain 0.1.17 and will be removed in 1.0. Use :meth:`~RunnableSequence, e.g., `prompt | llm`` instead.
  rerankChain = LLMChain(llm=llm, prompt=rerankPrompt,output_key="reranked_responses")


In [10]:
# prompt: download qs as json file. qs is a list of dataframes, formed using the python code below:
# uploaded = files.upload()
#     filename = next(iter(uploaded))
#     with open(filename,'r') as file:
#         loaded_list = json.load(file)
#   # Convert the list of dictionaries back to DataFrames
#   qs = [pd.DataFrame(df) for df in loaded_list]

import json
from google.colab import files

def save_qs_as_json(qs, filename="qs_data.json"):
  """Saves the list of dataframes (qs) as a JSON file.

  Args:
    qs: A list of pandas DataFrames.
    filename: The name of the JSON file to be saved.
  """
  try:
    # Convert each DataFrame to a list of dictionaries
    qs_list = [df.to_dict(orient='records') for df in qs]

    # Save the list of dictionaries as a JSON file
    with open(filename, 'w') as f:
      json.dump(qs_list, f, indent=4)

    files.download(filename)  # Download the file
    print(f"Data saved to {filename} and downloaded.")

  except Exception as e:
    print(f"An error occurred: {e}")

# Example usage (assuming 'qs' is defined as in your provided code):
# Replace with your actual 'qs' variable.
# This example assumes you have a 'qs' variable already in your colab environment.
# If you do not have it, load it first as in your original code.
# For this example, we'll just create some dummy data.
#import pandas as pd
#qs = [pd.DataFrame({'A': [1, 2], 'B': [3, 4]}), pd.DataFrame({'C': [5, 6], 'D': [7, 8]})]

#save_qs_as_json(qs) #Save and download the JSON file


### LLM-based functions for identifying Themes.

1. Identifies similar clusters of responses based on embeddings. (Uses UMAP to reduce dimensionality & HDBSCAN to cluster)
2. Prompts LLM to label clusters given a sample of responses from the cluster.
3. Prompts LLM to merge any similar clusters, and re-applies merged labels.

In [11]:
!pip install -U umap-learn
!pip install hdbscan

In [12]:
# Import UMAP from umap.umap_ instead of just importing umap
import umap.umap_ as umap
import hdbscan
from concurrent.futures import ThreadPoolExecutor

client = OpenAI()


def prepare_embeddings_for_clustering(qs, qid):
    """
    Prepare embeddings from qs[qid] for clustering.
    Returns numpy array of embeddings and list of corresponding response texts.
    """
    embeddings = []
    texts = []

    # Get embeddings and corresponding texts
    # Reset index to align with range(len(qs[qid]['embedding']))
    df = qs[qid].reset_index(drop=True)
    for idx in range(len(qs[qid]['embedding'])):
        if qs[qid]['embedding'][idx] is not None:  # Skip None embeddings
            embeddings.append(qs[qid]['embedding'][idx])
            texts.append(qs[qid]['English Responses'][idx])

    return np.array(embeddings), texts

def discover_themes(qs, qid, n_neighbors=15, min_cluster_size=5, min_samples=5):
    """
    Perform theme discovery using UMAP and HDBSCAN.
    Returns cluster labels and reduced embeddings.
    """
    # Prepare data
    embeddings, texts = prepare_embeddings_for_clustering(qs, qid)

    # Reduce dimensionality with UMAP
    reducer = umap.UMAP(n_neighbors=n_neighbors, random_state=42)
    reduced_embeddings = reducer.fit_transform(embeddings)

    # Cluster with HDBSCAN
    clusterer = hdbscan.HDBSCAN(
        min_cluster_size=min_cluster_size,
        min_samples=min_samples,
        metric='euclidean',
        cluster_selection_method='eom'
    )
    cluster_labels = clusterer.fit_predict(reduced_embeddings)

    return cluster_labels, reduced_embeddings, texts

def label_clusters_with_llm(cluster_labels, texts, model="gpt-4-turbo-preview", word_limit=4):
    """
    Use LLM to label clusters based on their content.
    Returns dictionary mapping cluster IDs to labels.
    """

    MAX_SAMPLE_OF_RESPONSES_TO_USE_FOR_LABELING = 50

    from openai import OpenAI
    client = OpenAI()

    # Group texts by cluster
    clusters = {}
    for label, text in zip(cluster_labels, texts):
        if label not in clusters:
            clusters[label] = []
        clusters[label].append(text)

    # Generate labels for each cluster
    cluster_labels = {}
    for cluster_id, cluster_texts in clusters.items():
        if cluster_id == -1:  # Skip noise points
            cluster_labels[cluster_id] = "Noise/Unclustered"
            continue

        # Prepare prompt with sample of texts
        sample_texts = cluster_texts[:MAX_SAMPLE_OF_RESPONSES_TO_USE_FOR_LABELING]
        prompt = f"""Analyze these responses and provide a concise 1-{word_limit} word phrase that either summarizes their shared meaning or, if more generality is needed, captures their common theme:

        Responses:
        {chr(10).join(sample_texts)}

        Shared meaning or Theme:"""

        # Get LLM response
        response = client.chat.completions.create(
            model=model,
            messages=[{"role": "user", "content": prompt}],
            temperature=0.3
        )

        cluster_labels[cluster_id] = response.choices[0].message.content.strip()

    return cluster_labels


def merge_similar_clusters(cluster_labels, reduced_embeddings, cluster_names, distance_threshold=0.5, similarity_threshold=0.8):
    """
    Merges similar clusters based on LLM evaluation and cluster distance,
    merging iteratively until no further merges are possible.
    """
    merged = True  # Flag to track if any merges occurred in the current iteration

    # Convert cluster_labels to a numpy array if it's not already
    cluster_labels = np.array(cluster_labels)

    while merged:
        merged = False  # Reset the flag for the current iteration

        # Get unique cluster IDs (excluding noise cluster -1)
        unique_clusters = np.unique(cluster_labels)
        unique_clusters = unique_clusters[unique_clusters != -1]

        if len(unique_clusters) <= 1:
            break  # No more clusters to merge

        # 1. Calculate Cluster Distances
        cluster_distances = calculate_cluster_distances(reduced_embeddings, cluster_labels)

        # print the average, median, min, and max cluster distances
        print(f"Average cluster distance: {np.mean(cluster_distances):.4f}")
        print(f"Median cluster distance: {np.median(cluster_distances):.4f}")
        print(f"Min cluster distance: {np.min(cluster_distances):.4f}")
        print(f"Max cluster distance: {np.max(cluster_distances):.4f}")

        # 2. Prepare Prompts for LLM
        prompts = []
        merge_candidates = []

        for i_idx, i in enumerate(unique_clusters):
            for j_idx, j in enumerate(unique_clusters[i_idx+1:], i_idx+1):
                # If the distance is within the threshold, proceed with LLM evaluation
                if cluster_distances[i_idx, j_idx] <= distance_threshold:
                    print(f"Cluster distance of {cluster_distances[i_idx, j_idx]:.4f} <= distance threshold {distance_threshold:.2f}")
                    print(f"Prompting LLM to compare clusters {cluster_names[i]} and {cluster_names[j]}")
                    distance = cluster_distances[i_idx, j_idx]
                    prompt = f"""Evaluate if these two theme labels should be merged into a single theme.
                    Themes should be specific enough for meaningful differentiation,
                    but broad enough for grouping similar responses under the same theme.

                    Theme 1: "{cluster_names[i]}"
                    Theme 2: "{cluster_names[j]}"
                    Distance measure: {distance:.4f} (lower means more similar)

                    Should these themes be merged? Answer with only 'yes' or 'no' and a brief explanation.


                    Examples:
                    Theme 1: "Anti-War"
                    Theme 2: "Promote Peace"
                    Response: no, because while both share a common goal, promoting peace can involve a wider range of actions beyond simply opposing war, such as conflict resolution, diplomacy, and building understanding between different groups.

                    Theme 1: "Anti-War"
                    Theme 2: "End conflict"
                    Response: yes, because being opposed to war is synonymous with wanting an end to conflict.
                    """

                    prompts.append(prompt)
                    merge_candidates.append((i, j))

        if not prompts:
            break  # No candidates to merge

        # 3. LLM Evaluation
        llm_responses = get_llm_responses(prompts)

        # 4. Process merges
        cluster_mapping = {label: label for label in unique_clusters}  # Initially, each cluster maps to itself

        for (i, j), llm_response in zip(merge_candidates, llm_responses):
            # Fixed: use 'in' operator instead of 'contains' method
            if "yes" in llm_response.lower():
                # Merge cluster j into cluster i
                cluster_mapping[j] = cluster_mapping[i]
                # Update the cluster name
                cluster_names[i] = f"{cluster_names[i]}/{cluster_names[j]}"
                merged = True  # Set the flag to indicate a merge occurred

        # Update cluster labels based on the mapping
        for idx, label in enumerate(cluster_labels):
            if label in cluster_mapping:
                cluster_labels[idx] = cluster_mapping[label]

        # Update cluster_names to remove merged clusters
        for old_label, new_label in cluster_mapping.items():
            if old_label != new_label:
                cluster_names[old_label] = None

        # Clean up cluster_names
        cluster_names = {k: v for k, v in cluster_names.items() if v is not None}

    return cluster_labels, cluster_names, cluster_distances


# Helper functions:

def calculate_cluster_distances(reduced_embeddings, cluster_labels):
  """
  Calculates the average Euclidean distance between clusters.

  Args:
    reduced_embeddings: The reduced embeddings of the data points.
    cluster_labels: The cluster labels for each data point.

  Returns:
    A distance matrix where element (i, j) represents the average distance
    between cluster i and cluster j.
  """
  unique_labels = np.unique(cluster_labels)
  num_clusters = len(unique_labels)
  distances = np.zeros((num_clusters, num_clusters))

  for i in range(num_clusters):
    for j in range(i + 1, num_clusters):
      cluster_i_points = reduced_embeddings[cluster_labels == unique_labels[i]]
      cluster_j_points = reduced_embeddings[cluster_labels == unique_labels[j]]

      # Calculate average distance between points in cluster i and cluster j
      avg_distance = np.mean([np.linalg.norm(p1 - p2)
                             for p1 in cluster_i_points
                             for p2 in cluster_j_points])
      distances[i, j] = avg_distance
      distances[j, i] = avg_distance  # Distance matrix is symmetric

  return distances





def get_llm_responses(prompts, model="gpt-4-turbo-preview", max_workers=10):
    """
    Calls the OpenAI API in parallel to get LLM responses for the given prompts.
    Returns:
        A list of LLM responses corresponding to the input prompts.
    """

    def get_response(prompt):
        response = client.chat.completions.create(
            model=model,
            messages=[{"role": "user", "content": prompt}],
            temperature=0.3
        )
        return response.choices[0].message.content.strip()

    with ThreadPoolExecutor(max_workers=max_workers) as executor:
        responses = list(executor.map(get_response, prompts))

    return responses


# Alternative approach: Instead of using cluster distance, just ask an LLM to
# merge similar themes after getting an initial list of cluster themes
def merge_themes_with_llm(qs, qid, cluster_names, model="gpt-4-turbo-preview"):
    """
    Prompts an LLM with a list of cluster names to identify themes to merge.
    Returns:
        1. A dictionary mapping original cluster IDs to merged theme names
        2. A dictionary containing information about which clusters were merged

    Args:
        cluster_names: Dictionary mapping cluster IDs to theme names
        model: The OpenAI model to use
    """
    # Skip if there are too few clusters to merge
    if len(cluster_names) <= 1:
        return cluster_names, {}

    # Create a list of themes with their original IDs for the prompt
    themes_with_ids = {i+1: (cluster_id, name) for i, (cluster_id, name) in enumerate(cluster_names.items())}

    # Create reverse mapping for parsing the response
    id_to_cluster_id = {i+1: cluster_id for i, (cluster_id, _) in enumerate(cluster_names.items())}

    # Format the themes list for the prompt
    prompt_list = [f"{i}. {name}" for i, (_, name) in themes_with_ids.items()]
    prompt_text = "\n".join(prompt_list)

    # get question text
    df = qs[qid]
    question_str = df["Question"][1]

    # Construct the prompt using JSON format for structured output
    prompt = f"""You are given a list of themes derived from clustering responses to the following survey question.
    Your task is to identify any themes that should be merged due to significant overlap or redundancy.

    Question:
    "{question_str}"

    Themes:
    {prompt_text}

    Please identify any themes that should be merged because they represent the same or very similar concepts.
    Respond with JSON in the following format:

    ```json
    {{
      "merges": [
        {{
          "merged_name": "New Theme Name",
          "original_indices": [1, 3, 5]
        }},
        {{
          "merged_name": "Another Theme Name",
          "original_indices": [2, 4]
        }}
      ]
    }}
    ```

    If no merges are recommended, respond with:
    ```json
    {{
      "merges": []
    }}
    ```

    The "original_indices" should contain the numbers of the themes from the list above that should be merged.
    The "merged_name" should be a concise, descriptive name that encompasses all merged themes.
    """

    # Call the LLM API
    import json

    response = client.chat.completions.create(
        model=model,
        messages=[{"role": "user", "content": prompt}],
        temperature=0.3,
        response_format={"type": "json_object"}  # Ensure JSON response
    )

    llm_output = response.choices[0].message.content.strip()

    # Parse the JSON response
    try:
        # Extract the JSON part from the response
        if "```json" in llm_output:
            json_str = llm_output.split("```json")[1].split("```")[0].strip()
        elif "```" in llm_output:
            json_str = llm_output.split("```")[1].strip()
        else:
            json_str = llm_output

        merge_data = json.loads(json_str)

        # Initialize output dictionaries
        merged_mapping = {cluster_id: name for cluster_id, name in cluster_names.items()}
        merge_info = {}

        # Process each merge
        for merge in merge_data.get("merges", []):
            merged_name = merge["merged_name"]
            original_indices = merge["original_indices"]

            # Get the original cluster IDs from the indices
            original_cluster_ids = [id_to_cluster_id[idx] for idx in original_indices]

            # Create merge information entry
            merge_info[merged_name] = {
                "original_names": [cluster_names[cluster_id] for cluster_id in original_cluster_ids],
                "cluster_ids": original_cluster_ids
            }

            # Update the mapping
            for cluster_id in original_cluster_ids:
                merged_mapping[cluster_id] = merged_name

        return merged_mapping, merge_info

    except (json.JSONDecodeError, KeyError) as e:
        print(f"Error parsing LLM response: {e}")
        print(f"Raw response: {llm_output}")
        # Return the original mapping if there's an error
        return cluster_names, {}


def apply_merged_themes(cluster_labels, merged_mapping):
    """
    Applies the merged theme mapping to original cluster labels.

    Args:
        cluster_labels: Original numeric cluster labels from HDBSCAN
        merged_mapping: Dictionary mapping original cluster IDs to merged theme names

    Returns:
        numeric_mapping: Dictionary mapping original cluster IDs to new consolidated cluster IDs
        new_cluster_names: Dictionary mapping new cluster IDs to theme names
    """
    # Create a mapping of theme names to new cluster IDs
    unique_themes = list(set(merged_mapping.values()))
    theme_to_id = {theme: i for i, theme in enumerate(unique_themes)}

    # Create mapping from original cluster IDs to new cluster IDs
    numeric_mapping = {}
    for original_id, theme_name in merged_mapping.items():
        numeric_mapping[original_id] = theme_to_id[theme_name]

    # Create new dictionary mapping new cluster IDs to theme names
    new_cluster_names = {theme_to_id[theme]: theme for theme in unique_themes}

    # Make sure noise cluster (-1) is preserved
    if -1 in cluster_labels:
        numeric_mapping[-1] = -1
        new_cluster_names[-1] = "Noise/Unclustered"

    return numeric_mapping, new_cluster_names


def apply_numeric_mapping(cluster_labels, numeric_mapping):
    """
    Applies the numeric mapping to cluster labels, preserving their numpy array format.

    Args:
        cluster_labels: Original numeric cluster labels from HDBSCAN
        numeric_mapping: Dictionary mapping original cluster IDs to new cluster IDs

    Returns:
        numpy array of new cluster labels
    """
    import numpy as np

    # Convert to numpy array if it's not already
    cluster_labels = np.array(cluster_labels)

    # Create new array with mapped values
    new_labels = np.array([numeric_mapping.get(label, -1) for label in cluster_labels])

    return new_labels


def save_themes_to_data(qs, qid, cluster_labels, texts, cluster_names, merge_info=None):
    """
    Saves theme information to the qs data structure for the given question ID.

    Args:
        qs: The data structure containing question data (list of pandas DataFrames)
        qid: The question ID to save themes for
        cluster_labels: The final cluster labels for each response
        texts: The response texts that were clustered
        cluster_names: Dictionary mapping cluster IDs to theme names
        merge_info: Optional dictionary with information about merged themes

    Returns:
        Updated qs data structure
    """
    import pandas as pd
    import numpy as np

    # Create the metadata dictionary for question-level themes info
    themes_metadata = {
        'cluster_names': cluster_names,
        'merge_info': merge_info if merge_info else None
    }

    # Store question-level metadata in a column called 'question_themes'
    if 'question_themes' not in qs[qid].columns:
        qs[qid]['question_themes'] = None

    # Check if index 0 exists, if not use the first available index
    if 0 not in qs[qid].index:
        first_idx = qs[qid].index[0]
        qs[qid].at[first_idx, 'question_themes'] = themes_metadata
    else:
        qs[qid].at[0, 'question_themes'] = themes_metadata

    # Create mapping from response text to theme
    response_to_theme = {}
    for text, label in zip(texts, cluster_labels):
        theme_name = cluster_names.get(label, "Unclustered")
        response_to_theme[text] = theme_name

    # Add or update 'response_theme' column for individual response themes
    if 'response_theme' not in qs[qid].columns:
        qs[qid]['response_theme'] = np.nan

    # Map each response to its theme
    for i, response in enumerate(qs[qid]['English Responses']):
        if i < len(qs[qid]) and response in response_to_theme:
            idx = qs[qid].index[i]
            qs[qid].at[idx, 'response_theme'] = response_to_theme[response]

    # Also add a 'cluster_id' column to store the numeric label
    if 'cluster_id' not in qs[qid].columns:
        qs[qid]['cluster_id'] = np.nan

    # Create mapping from text to cluster ID
    text_to_cluster = {text: label for text, label in zip(texts, cluster_labels)}

    # Assign cluster IDs to each response
    for i, response in enumerate(qs[qid]['English Responses']):
        if i < len(qs[qid]) and response in text_to_cluster:
            idx = qs[qid].index[i]
            qs[qid].at[idx, 'cluster_id'] = int(text_to_cluster[response])

    return qs


def reclassify_unclustered_responses(qs, qid, batch_size=50, model="gpt-4-turbo-preview"):
    """
    Uses an LLM to attempt to classify unclustered responses into existing themes.

    Args:
        qs: The data structure containing question data
        qid: The question ID to process
        batch_size: Number of responses to process in each batch (to avoid API limits)
        model: The OpenAI model to use

    Returns:
        Updated qs data structure with reclassified responses
    """
    import pandas as pd
    import numpy as np

    # Get the DataFrame for the question
    df = qs[qid]

    # Get question text - check if it exists
    question_str = None
    if 'Question' in df.columns and len(df) > 0:
        # Get from the first available row
        question_str = df.iloc[0]['Question']
        if pd.isna(question_str) and len(df) > 1:
            question_str = df.iloc[1]['Question']

    if not question_str:
        question_str = f"Question {qid}"  # Fallback if question text not found

    # Check if required columns exist
    if 'response_theme' not in df.columns:
        raise ValueError("Column 'response_theme' not found. Run save_themes_to_data first.")

    if 'question_themes' not in df.columns:
        raise ValueError("Column 'question_themes' not found. Run save_themes_to_data first.")

    # Get theme metadata from the first row that has it
    themes_metadata = None
    for idx in df.index:
        if not pd.isna(df.at[idx, 'question_themes']):
            themes_metadata = df.at[idx, 'question_themes']
            break

    if not themes_metadata or 'cluster_names' not in themes_metadata:
        raise ValueError("Theme metadata not found or invalid.")

    # Get available themes (excluding "Noise/Unclustered")
    available_themes = [theme for theme_id, theme in themes_metadata['cluster_names'].items()
                       if theme != "Noise/Unclustered"]

    if not available_themes:
        print("No valid themes found for reclassification.")
        return qs

    # Create a formatted string of available themes for the prompt
    themes_formatted = "\n".join([f"{i+1}. {theme}" for i, theme in enumerate(available_themes)])

    # Find unclustered responses
    unclustered_mask = df['response_theme'] == "Noise/Unclustered"
    unclustered_indices = df[unclustered_mask].index.tolist()

    if not unclustered_indices:
        print("No unclustered responses found.")
        return qs

    print(f"Found {len(unclustered_indices)} unclustered responses. Attempting reclassification...")

    # Create prompts for each unclustered response
    prompts = []
    batch_indices = []

    for idx in unclustered_indices:
        response_text = df.at[idx, 'English Responses']

        # Skip empty responses
        if pd.isna(response_text) or response_text.strip() == "":
            continue

        prompt = f"""Evaluate if the following response to the question below can be classified into one of the existing themes.

Question:
"{question_str}"

Response:
"{response_text}"

Available themes:
{themes_formatted}

Steps:
1. Analyze the response's core meaning or intent
2. Compare it to the available themes
3. If the response clearly matches a theme, select that theme
4. If the response doesn't clearly match any theme, select "None"

Return ONLY the theme number or "None" with no explanation or additional text.
"""

        prompts.append(prompt)
        batch_indices.append(idx)

    # Process responses in batches
    all_classifications = []

    for i in range(0, len(prompts), batch_size):
        batch_prompts = prompts[i:i+batch_size]
        batch_idx = batch_indices[i:i+batch_size]

        print(f"Processing batch {i//batch_size + 1}/{(len(prompts) + batch_size - 1)//batch_size}...")

        # Get LLM responses using the provided function
        batch_responses = get_llm_responses(batch_prompts, model=model)

        # Process the responses
        for idx, response in zip(batch_idx, batch_responses):
            response = response.strip()

            # Try to parse as a number
            try:
                theme_num = int(response)
                if 1 <= theme_num <= len(available_themes):
                    selected_theme = available_themes[theme_num - 1]
                    df.at[idx, 'response_theme'] = selected_theme
                    all_classifications.append((idx, selected_theme))
                else:
                    # Number out of range
                    pass
            except ValueError:
                # Not a number, check if it's a theme name directly
                if response in available_themes:
                    df.at[idx, 'response_theme'] = response
                    all_classifications.append((idx, response))
                # Otherwise, leave as "Noise/Unclustered"

    # Print results
    reclassified_count = len(all_classifications)
    print(f"Reclassification complete. {reclassified_count} of {len(unclustered_indices)} responses were reclassified.")

    return qs

# Example usage:
"""
# After running save_themes_to_data:
qs = reclassify_unclustered_responses(qs, qid)

# To visualize the result:
fig, axes = plot_theme_distribution(qs, qid)
plt.show()
"""



def plot_themes(reduced_embeddings, cluster_labels, cluster_names):
    """
    Plot the clustered embeddings with their labels.
    """
    import matplotlib.pyplot as plt

    plt.figure(figsize=(12, 8))
    scatter = plt.scatter(
        reduced_embeddings[:, 0],
        reduced_embeddings[:, 1],
        c=cluster_labels,
        cmap='tab20'
    )

    # Add legend
    legend_elements = [
        plt.Line2D([0], [0], marker='o', color='w',
                  label=cluster_names[label],
                  markerfacecolor=scatter.cmap(scatter.norm(label)))
        for label in set(cluster_labels) if label != -1
    ]
    plt.legend(handles=legend_elements, title="Themes", bbox_to_anchor=(1.05, 1))

    plt.title("Question Response Themes")
    plt.xlabel("UMAP Dimension 1")
    plt.ylabel("UMAP Dimension 2")
    plt.tight_layout()
    plt.show()


def plot_clusters(qs, qid, figsize=(12, 8), title=None, marker_size=50, show_legend=True,
                  legend_cols=1, highlight_cluster=None, show_unclustered=True):
    """
    Plot the clustered embeddings with their labels, reading directly from the qs structure.
    The function re-runs the initial clustering steps to ensure proper visualization.

    Args:
        qs: The data structure containing question data
        qid: The question ID to visualize
        figsize: Size of the figure as a tuple (width, height)
        title: Custom title for the plot (default: auto-generated based on qid)
        marker_size: Size of the scatter plot markers
        show_legend: Whether to show the legend
        legend_cols: Number of columns in the legend
        highlight_cluster: Cluster ID or name to highlight (others will be faded)
        show_unclustered: Whether to show unclustered points (noise)

    Returns:
        Matplotlib figure and axes objects
    """
    import matplotlib.pyplot as plt
    import numpy as np
    import pandas as pd
    from matplotlib.lines import Line2D

    # Get the DataFrame for the question
    df = qs[qid]

    # Check if we have the necessary columns
    if 'cluster_id' not in df.columns or 'response_theme' not in df.columns:
        raise ValueError("Missing required columns 'cluster_id' or 'response_theme'. Run save_themes_to_data first.")

    # Get theme metadata
    themes_metadata = None
    for idx in df.index:
        if 'question_themes' in df.columns and not pd.isna(df.at[idx, 'question_themes']):
            themes_metadata = df.at[idx, 'question_themes']
            break

    if not themes_metadata or 'cluster_names' not in themes_metadata:
        raise ValueError("Theme metadata not found or invalid. Run save_themes_to_data first.")

    # Simply re-run the discover_themes function to get embeddings and cluster labels
    print("Running dimensionality reduction and clustering...")

    # Use the discover_themes function which correctly handles your data format
    from umap.umap_ import UMAP
    import hdbscan

    # Prepare embeddings for clustering (directly without using the function)
    embeddings = []
    texts = []

    # Get embeddings and corresponding texts safely
    for idx in range(len(df['embedding'])):
        try:
            embedding_val = df['embedding'].iloc[idx]
            if embedding_val is not None and isinstance(embedding_val, (list, np.ndarray)) and len(embedding_val) > 0:
                embeddings.append(embedding_val)
                texts.append(df['English Responses'].iloc[idx])
        except (TypeError, ValueError):
            continue

    if not embeddings:
        raise ValueError("No valid embeddings found for visualization.")

    embeddings_array = np.array(embeddings)

    # Run dimensionality reduction with UMAP
    reducer = UMAP(n_neighbors=15, random_state=42)
    reduced_embeddings = reducer.fit_transform(embeddings_array)

    # Get the existing cluster IDs for these texts
    text_to_cluster_id = {}
    text_to_theme = {}

    for idx in df.index:
        if pd.notna(df.at[idx, 'response_theme']) and pd.notna(df.at[idx, 'cluster_id']):
            text = df.at[idx, 'English Responses']
            text_to_cluster_id[text] = int(df.at[idx, 'cluster_id'])
            text_to_theme[text] = df.at[idx, 'response_theme']

    # Map reduced embeddings to their cluster IDs and themes
    cluster_ids = []
    themes = []

    for text in texts:
        cluster_id = text_to_cluster_id.get(text, -1)  # Default to noise cluster
        theme = text_to_theme.get(text, "Noise/Unclustered")
        cluster_ids.append(cluster_id)
        themes.append(theme)

    # Convert to numpy arrays for filtering
    cluster_ids = np.array(cluster_ids)
    themes = np.array(themes)

    # Create figure and axis
    fig, ax = plt.subplots(figsize=figsize)

    # Get coordinates for plotting
    x_coords = reduced_embeddings[:, 0]
    y_coords = reduced_embeddings[:, 1]

    # Filter out unclustered points if needed
    if not show_unclustered:
        mask = cluster_ids != -1
        x_coords = x_coords[mask]
        y_coords = y_coords[mask]
        cluster_ids = cluster_ids[mask]
        themes = themes[mask]

    # Apply highlighting if specified
    highlight_mask = None
    if highlight_cluster is not None:
        if isinstance(highlight_cluster, str):
            # Highlight by theme name
            highlight_mask = themes == highlight_cluster
        else:
            # Highlight by cluster ID
            highlight_mask = cluster_ids == highlight_cluster

    # Create the scatter plot
    scatter = ax.scatter(
        x_coords,
        y_coords,
        c=cluster_ids,
        cmap='tab20',
        s=marker_size,
        alpha=0.7 if highlight_mask is None else np.where(highlight_mask, 1.0, 0.2)
    )

    # Create legend
    if show_legend:
        # Get unique cluster IDs (excluding noise if not showing it)
        unique_ids = sorted(set(cluster_ids))
        if not show_unclustered and -1 in unique_ids:
            unique_ids.remove(-1)

        # Create legend elements
        legend_elements = []
        for label in unique_ids:
            if label == -1:
                name = "Noise/Unclustered"
            else:
                name = themes_metadata['cluster_names'].get(label, f"Cluster {label}")

            legend_elements.append(
                Line2D([0], [0], marker='o', color='w', markerfacecolor=scatter.cmap(scatter.norm(label)),
                      markersize=10, label=name)
            )

        # Add the legend
        ax.legend(
            handles=legend_elements,
            title="Themes",
            loc='center left',
            bbox_to_anchor=(1, 0.5),
            ncol=legend_cols
        )

    # Set title and labels
    if title is None:
        # Try to get the question text
        question_text = None
        if 'Question' in df.columns:
            for idx in df.index:
                if pd.notna(df.at[idx, 'Question']):
                    question_text = df.at[idx, 'Question']
                    break

        if question_text:
            # Truncate long questions
            if len(question_text) > 70:
                question_text = question_text[:67] + "..."
            title = f"Question {qid}: {question_text}"
        else:
            title = f"Question {qid} Response Themes"

    ax.set_title(title, fontsize=14, fontweight='bold')
    ax.set_xlabel("UMAP Dimension 1")
    ax.set_ylabel("UMAP Dimension 2")

    # Add summary information
    summary_text = (
        f"Total points: {len(x_coords)}\n"
        f"Number of clusters: {len([l for l in unique_ids if l != -1])}"
    )

    plt.figtext(0.02, 0.02, summary_text, fontsize=10, bbox=dict(facecolor='white', alpha=0.8))

    # Adjust layout
    plt.tight_layout()

    return fig, ax



def plot_theme_distribution(qs, qid, min_percentage=1, sort_by='count', figsize=(12, 8)):
    """
    Creates a visualization of theme distribution for a specific question.

    Args:
        qs: The data structure containing question data
        qid: The question ID to visualize
        min_percentage: Minimum percentage for a theme to be shown separately (smaller will be grouped as 'Other')
        sort_by: How to sort the bars - 'count' (default), 'alphabetical', or 'percentage'
        figsize: Size of the figure as a tuple (width, height)

    Returns:
        Matplotlib figure and axes objects
    """
    import matplotlib.pyplot as plt
    import pandas as pd
    import numpy as np

    # Get the DataFrame for the question
    df = qs[qid]

    # Check if response_theme column exists
    if 'response_theme' not in df.columns:
        raise ValueError("Column 'response_theme' not found. Run save_themes_to_data first.")

    # Count occurrences of each theme
    theme_counts = df['response_theme'].value_counts()
    total_responses = len(df)
    theme_percentages = (theme_counts / total_responses) * 100

    # Combine themes with percentage less than min_percentage into 'Other'
    small_themes = theme_percentages[theme_percentages < min_percentage].index
    if not small_themes.empty:
        # Create a copy to avoid modifying the original DataFrame
        df_copy = df.copy()
        df_copy.loc[df_copy['response_theme'].isin(small_themes), 'response_theme'] = 'Other'

        # Recalculate counts and percentages
        theme_counts = df_copy['response_theme'].value_counts()
        theme_percentages = (theme_counts / total_responses) * 100

    # Create a DataFrame for plotting
    plot_data = pd.DataFrame({
        'Count': theme_counts,
        'Percentage': theme_percentages
    })

    # Sort the data
    if sort_by == 'count':
        plot_data = plot_data.sort_values('Count', ascending=False)
    elif sort_by == 'alphabetical':
        plot_data = plot_data.sort_index()
    elif sort_by == 'percentage':
        plot_data = plot_data.sort_values('Percentage', ascending=False)

    # Create figure and axis
    fig, ax1 = plt.subplots(figsize=figsize)

    # Plot counts as bars
    bars = ax1.bar(plot_data.index, plot_data['Count'], color='steelblue')
    ax1.set_xlabel('Theme')
    ax1.set_ylabel('Count', color='steelblue')
    ax1.tick_params(axis='y', labelcolor='steelblue')

    # Rotate x-axis labels for better readability
    plt.xticks(rotation=45, ha='right')

    # Create a second y-axis for percentages
    ax2 = ax1.twinx()
    ax2.set_ylabel('Percentage (%)', color='red')
    ax2.plot(plot_data.index, plot_data['Percentage'], 'ro-')
    ax2.tick_params(axis='y', labelcolor='red')

    # Add percentage labels above each bar
    for i, bar in enumerate(bars):
        percentage = plot_data['Percentage'].iloc[i]
        count = plot_data['Count'].iloc[i]
        ax1.text(
            bar.get_x() + bar.get_width()/2,
            bar.get_height() + 0.5,
            f'{percentage:.1f}%\n({count})',
            ha='center',
            va='bottom',
            fontweight='bold'
        )

    # Add title
    plt.title(f'Theme Distribution for Question {qid}', fontsize=14, fontweight='bold')

    # Add summary information
    total_themes = len(plot_data)
    primary_theme = plot_data.index[0] if not plot_data.empty else "None"
    primary_percentage = plot_data['Percentage'].iloc[0] if not plot_data.empty else 0

    summary_text = (
        f'Total Responses: {total_responses}\n'
        f'Number of Themes: {total_themes}\n'
        f'Primary Theme: {primary_theme} ({primary_percentage:.1f}%)'
    )

    plt.figtext(0.02, 0.02, summary_text, fontsize=10, bbox=dict(facecolor='white', alpha=0.8))

    # Adjust layout
    plt.tight_layout()

    # Return figure and axes for further customization if needed
    return fig, (ax1, ax2)

# Example usage:
"""
# After running save_themes_to_data:
fig, axes = plot_theme_distribution(qs, qid)
plt.show()

# With customization:
fig, axes = plot_theme_distribution(
    qs,
    qid,
    min_percentage=2,  # Group themes with <2% representation as 'Other'
    sort_by='alphabetical',  # Sort themes alphabetically
    figsize=(14, 10)  # Larger figure
)
plt.show()
"""

def get_responses_by_theme(qs, qid, theme_name, max_responses=None, return_dataframe=False):
    """
    Retrieves all responses tagged with a specific theme.

    Args:
        qs: The data structure containing question data
        qid: The question ID to analyze
        theme_name: The theme name to filter by
        max_responses: Maximum number of responses to return (None for all)
        return_dataframe: If True, returns a DataFrame; if False, returns a list of responses

    Returns:
        Either a list of responses or a DataFrame, depending on return_dataframe parameter
    """
    import pandas as pd

    # Get the DataFrame for the question
    df = qs[qid]

    # Check if required column exists
    if 'response_theme' not in df.columns:
        raise ValueError("Column 'response_theme' not found. Run save_themes_to_data first.")

    # Filter responses with the specified theme
    filtered_df = df[df['response_theme'] == theme_name].copy()

    # Sort by cluster_id if available
    if 'cluster_id' in filtered_df.columns:
        filtered_df = filtered_df.sort_values('cluster_id')

    # Limit the number of responses if specified
    if max_responses is not None and max_responses > 0:
        filtered_df = filtered_df.head(max_responses)

    if return_dataframe:
        return filtered_df
    else:
        # Return just the responses as a list
        responses = filtered_df['English Responses'].tolist()
        return responses

# Example usage:
"""
# Get all responses for a specific theme
responses = get_responses_by_theme(qs, qid, "Peace and Unity")

# Print the first 5 responses
for i, response in enumerate(responses[:5], 1):
    print(f"{i}. {response}")
    print("-" * 40)

# Or get the entire DataFrame with all columns
theme_df = get_responses_by_theme(qs, qid, "Peace and Unity", return_dataframe=True)
"""


# Example usage workflow:
"""
# Step 1: Discover themes
cluster_labels, reduced_embeddings, texts = discover_themes(qs, qid)

# Step 2: Label clusters
cluster_names = label_clusters_with_llm(cluster_labels, texts)

# Step 3: Merge similar clusters by LLM recognition of theme similarity
merged_mapping, merge_info = merge_themes_with_llm(qs, qid, cluster_names)

# Step 4: Apply merged themes to get new numeric labels and theme names
numeric_mapping, new_cluster_names = apply_merged_themes(cluster_labels, merged_mapping)
new_cluster_labels = apply_numeric_mapping(cluster_labels, numeric_mapping)

# Step 5: Save themes to the data structure
qs = save_themes_to_data(qs, qid, new_cluster_labels, texts, new_cluster_names, merge_info)

# Step 6: Reclassify unclustered responses
qs = reclassify_unclustered_responses(qs, qid)

# Step 7: Visualize the results
plot_theme_distribution(qs, qid)
fig, ax = plot_clusters(qs, qid, show_unclustered=False)
plt.show()

# Step 8: Look at some individual responses by theme
responses = get_responses_by_theme(qs, qid, "Peace and Unity", max_responses=5)
for i, response in enumerate(responses, 1):
    print(f"{i}. {response}")
"""

'\n# Step 1: Discover themes\ncluster_labels, reduced_embeddings, texts = discover_themes(qs, qid)\n\n# Step 2: Label clusters\ncluster_names = label_clusters_with_llm(cluster_labels, texts)\n\n# Step 3: Merge similar clusters by LLM recognition of theme similarity\nmerged_mapping, merge_info = merge_themes_with_llm(qs, qid, cluster_names)\n\n# Step 4: Apply merged themes to get new numeric labels and theme names\nnumeric_mapping, new_cluster_names = apply_merged_themes(cluster_labels, merged_mapping)\nnew_cluster_labels = apply_numeric_mapping(cluster_labels, numeric_mapping)\n\n# Step 5: Save themes to the data structure\nqs = save_themes_to_data(qs, qid, new_cluster_labels, texts, new_cluster_names, merge_info)\n\n# Step 6: Reclassify unclustered responses\nqs = reclassify_unclustered_responses(qs, qid)\n\n# Step 7: Visualize the results\nplot_theme_distribution(qs, qid)\nfig, ax = plot_clusters(qs, qid, show_unclustered=False)\nplt.show()\n\n# Step 8: Look at some individual respon

# Analysis library usage examples

### List questions and segments by ID for reference

In [3]:
# show questions by type and ID
# this ID aka "qid" is what is used to reference the question in the other analysis functons
show_questions(qs)

question type  \
0   Poll Single Select   
1   Poll Single Select   
2   Poll Single Select   
3   Poll Single Select   
4   Poll Single Select   
..                 ...   
61  Poll Single Select   
62  Ask Opinion          
63  Poll Single Select   
64  Poll Single Select   
65  Ask Experience       

                                                                                                                                                                                question text  
0   Please select your preferred language:                                                                                                                                                     
1   How old are you?                                                                                                                                                                           
2   What is your gender?                                                                                                                                                                       
3   What best describes where you live?                                                                                                                                                        
4   Overall, would you say the increased use of artificial intelligence (AI) in daily life makes you feel…                                                                                     
..                                                                                                     ...                                                                                     
61  Do you agree or disagree?                                                                                                                                                                  
62  Please explain whether you agree or disagree and why.                                                                                                                                      
63  Do you feel you were able to fully express your views on your culture, your values, and what you want for the future in this conversation? (through what you responded and how you voted)  
64  Do you feel like you understand yourself better after participating in this conversation?                                                                                                  
65  Lastly, is there anything you felt you could not express in this conversation that you want to make sure the people working on this know?                                                  

[66 rows x 2 columns]

In [ ]:
# list the sgements by their ID
# these IDs are what are used to reference segments in other analysis functions
# common usage of segments IDs si: segs = [0,1] to do analysis comparing segments 0 and 1
show_segments(qs)

### Plot poll results

In [ ]:
#choose question and segments
qid = 25

segs = [0]

#plot
d = plot_poll(qs[qid],segs)

### Ranking and displaying responses to collective response prompts

#### Basic
First we'll create a simple visualization of the results of a **collective response** question (aka "ask opinion" on Remesh) where users respond with natural language and then vote on the responses submitted by others. The visualization is generated for a selected *question* and *set of segments*. In the visualization each row corresponds to a response, columns correspond to the selected set of segments, and values correspond to the fraction of each segment which  agrees* with each response.

*this agreement fraction is computed on Remesh using [elicitation inference](https://openreview.net/pdf?id=tkxnRPkb_H). We sample around 10-30 votes per person, then infer the rest. Accuracy of individual vote inferences is 75-80%, and the aggregated agreement fraction values for each segment have a 1 stdv confidence range of around +/- 1-3% relative to the participant sample*

In [ ]:
#choose question and segments
qid = 21
segs = segs = [231,232,233,234,235,236,0]

#print the question text
print(qs[qid]["Question"][1])

#visualize table of results with the first 5 responses
table_ask(qs[qid],segs,15)

#### Rank by bridging, polarization, and divergence

Now we'll create the same table, but add metrics for bridging, polarizaiton, and divergence. We'll use the "bridging_ask" function that automatically ranks by the bridging metric.

- **The bridging metric** is meant to capture the degree to which there is agreement for a response across ALL specified population segments; even those which typically disagree. To capture this we use the segment-level analouge of a Max-Min social wellfare function. If a_ij is the fraction of the j^th segment which agrees with i^th response, then we compute the bridging metric for that response as b_i = MIN(a_i1,a_i2,...,a_iN)

- **The polarization metric** is meant to capture the degree to which there is polariation between specified segments about a response. To capture this we compute the difference in agreement fraction for the segments which most agree with the response and least agree with the response. ie p_i = MAX(a_i1,a_i2,...,a_iN) - MIN(a_i1,a_i2,...,a_iN)

- **The divergence metric** is meant to capture the degree to which there is a minority vs majority split between specified segments about a response. ie. where the majority of one segment agrees with a response but a majority of another segment disagrees with it.  To capture this we compute the geometric mean of how far away the highest and lowest agreement segments are from 50% agreement. ie d_i = SQRT(MAX(dmax_i-0.5,0)*MAX((0.5-dmin)_i,0)), where dmax_i = MAX(a_i1,a_i2,...,a_iN) and dmin_i = MIN(a_i1,a_i2,...,a_iN)

In [ ]:
#choose question and segments
qid = 21
segs = segs = [231,232,233,234,235,236,0]

#print the question
print(qs[qid]["Question"][1])

#generate a table with bridging, polarization, and consensus metrics; keeping the 5 responses with the hightest bridging agreement
ba = bridging_ask(qs[qid],segs).iloc[:5]

#display a pretty version fo the table
ba.style.pipe(make_pretty)

We can show responses with the highest divergence in a similar manner using the *get_divergent_responses* funciton.

In [ ]:
#choose question and segments
qid = 21
segs = segs = [231,232,233,234,235,236,0]

#print the question
print(qs[qid]["Question"][1])

#generate a table with bridging, polarization, and consensus metrics; keeping the 5 responses with the hightest polarization
ba = get_divergent_responses(qs[qid],segs,5)

#display a pretty version fo the table
ba.style.pipe(make_pretty)

#### Rank by relevence

We use the *rank_by_similarity* function to rank responses by relevance to a given term, topic, phrase, or question

In [ ]:
#choose question and segments
qid = 24
segs = segs = [231,232,233,234,235,236,0]

#text we want responses to be relevant to
text = "the next generation of children"

#print the question
print(qs[qid]["Question"][1])

#generate a table with responsees ranked by relatedness to the search text
ba = rank_by_similarity(qs[qid], text)

#display a pretty version of the table the top 5 most relevant responses and agreement data for the given segments
table_ask(ba,segs,5)

### LLM result synthesis

#### Generate a **bullet point summary** of ideas in bridging responses

In [ ]:
#select question and segments
qid = 24
segs = segs = [0]

#set the params for the
synth_type = "bullets"      #synthesize results as bullet points
rank_type = "bridging"      #ranking responses to synthesize by bridgage agreement across [segs]
thresh = .50                #only keep responses where 50%+ participants in all [segs] agree
n_max = 50                  #only keep the top 50 responses withi highest bridging agreement
query_text = ""             #set blank to not focus on any particular topic

#run the sytthesis
out = synthesize(qs,qid,segs,synth_type,rank_type,thresh,n_max,query_text = query_text)

#print quesiton text
print(qs[qid]["Question"].iloc[0])

#print synthesis results
print(out[synth_type])

#### Generate a **taxonomy summarizing ideas** from bridging responses related to *healthcare*

In [ ]:
#select question and segments
qid = 27
segs = segs = [0]

#set the params for the
synth_type = "summary"      #synthesize results as taxonomic summary
rank_type = "bridging"      #ranking responses to synthesize by bridgage agreement across [segs]
thresh = .50                #only keep responses where 50%+ participants in all [segs] agree
n_max = 1000                #only keep the top 100 responses withi highest bridging agreement
query_text = ""   #focus on resposnes and sythesized results related to "healthcare"

#run the sytthesis
out = synthesize(qs,qid,segs,synth_type,rank_type,thresh,n_max,query_text = query_text)

#print quesiton text
print(qs[qid]["Question"].iloc[0])

#print synthesis results
print(out[synth_type])

#### Generate a set of **outcomes** related to *healthcare*


In [ ]:
#select question and segments
qid = 21
segs = segs = [231,232,233,234,235]

#set the params for the
synth_type = "outcomes"      #synthesize result into outcomes
rank_type = "relevance"      #ranking responses to synthesize by bridgage agreement across [segs]
thresh = .33                #only keep responses where cosine similarity with query_text is >0.33
n_max = 100                 #only keep the top 100 responses withi highest bridging agreement
query_text = "human-AI relationships"  #focus on resposnes and sythesized results related to "climate"

#run the sytthesis
out = synthesize(qs,qid,segs,synth_type,rank_type,thresh,n_max,query_text = query_text)

#print quesiton text
print(qs[qid]["Question"][1])

#print synthesis results
print(out[synth_type])

#show the top 10 most relevant responses used in the synthesis along with their agreement across contintents
dat = out["data"]
table_ask(dat,segs,10)

## Get Themes of Feedback on the Survey

In [ ]:
qid = 27 # Feedback question
#print quesiton text
print(qs[qid]["Question"][1])

# Step 1: Discover themes
cluster_labels, reduced_embeddings, texts = discover_themes(qs, qid)

# Step 2: Label clusters
cluster_names = label_clusters_with_llm(cluster_labels, texts)

# Step 3: Merge similar clusters by LLM recognition of theme similarity
merged_mapping, merge_info = merge_themes_with_llm(qs, qid, cluster_names)

# Step 4: Apply merged themes to get new numeric labels and theme names
numeric_mapping, new_cluster_names = apply_merged_themes(cluster_labels, merged_mapping)
new_cluster_labels = apply_numeric_mapping(cluster_labels, numeric_mapping)

# Step 5: Save themes to the data structure
qs = save_themes_to_data(qs, qid, new_cluster_labels, texts, new_cluster_names, merge_info)

# Step 6: Reclassify unclustered responses
qs = reclassify_unclustered_responses(qs, qid)

# Step 7: Visualize the results
plot_theme_distribution(qs, qid)
fig, ax = plot_clusters(qs, qid, show_unclustered=False)
plt.show()

In [ ]:
responses = get_responses_by_theme(qs, qid, "General Satisfaction/Positive Feedback")
for i, response in enumerate(responses, 1):
    print(f"{i}. {response}")

In [ ]:
save_data_to_drive(qs)

# Global Dialogues Cadence Analysis

## GD Indicators

In [14]:
pd.set_option('display.max_rows', None)
show_questions(qs)
indicator_questions = [4,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28]
indicator_questions = {
    'Risks':[]
                       }

In [ ]:
qs[]

In [ ]:
# prompt: I want to output a dataframe that shows the comma-delimited-joined "Responses" for each dataframe at every index in qs where qs[i]["Question Type"] == "Poll Single Select"
# For example, the output of qs[35]["Responses] is a df:
# Responses
# 0	Profoundly Worse
# 1	Noticeably Worse
# 2	No Major Change
# 3	Noticeably Better
# 4	Profoundly Better
# and the output of qs[35]["Question Type"] is a dataframe:
# 	Question Type
# 0	Poll Single Select
# 1	Poll Single Select
# 2	Poll Single Select
# 3	Poll Single Select
# 4	Poll Single Select
# qs is a list of dataframes. Make this as simple and straightforward using standard pandas pd dataframe practices/tricks to do this like a regular data scientist in a python notebook would do

import pandas as pd

def get_poll_responses(qs):
  """
  Returns a DataFrame with comma-delimited "Responses" for each DataFrame
  where "Question Type" is "Poll Single Select".
  """

  poll_data = []
  for i in range(len(qs)):
    if "Question Type" in qs[i].columns and all(qs[i]["Question Type"] == "Poll Single Select"):
      responses = ", ".join(qs[i]["Responses"].astype(str))
      poll_data.append({"Index": i, "Responses": responses})
  return pd.DataFrame(poll_data)

# Example usage (assuming 'qs' is defined as in your provided code):
result_df = get_poll_responses(qs)
result_df


In [ ]:
qs[35]["Responses"]
get_poll_responses(qs)

In [20]:
show_questions(qs)

question type  \
0   Poll Single Select   
1   Poll Single Select   
2   Poll Single Select   
3   Poll Single Select   
4   Poll Single Select   
5   Poll Single Select   
6   Poll Single Select   
7   Poll Single Select   
8   Poll Single Select   
9   Poll Single Select   
10  Poll Single Select   
11  Poll Single Select   
12  Poll Single Select   
13  Poll Single Select   
14  Ask Experience       
15  Poll Single Select   
16  Poll Single Select   
17  Poll Single Select   
18  Poll Single Select   
19  Poll Single Select   
20  Poll Single Select   
21  Poll Single Select   
22  Poll Single Select   
23  Poll Single Select   
24  Poll Single Select   
25  Poll Single Select   
26  Poll Single Select   
27  Poll Single Select   
28  Poll Single Select   
29  Poll Single Select   
30  Poll Single Select   
31  Poll Single Select   
32  Poll Single Select   
33  Ask Opinion          
34  Poll Single Select   
35  Poll Single Select   
36  Poll Single Select   
37  Poll Single Select   
38  Poll Single Select   
39  Poll Single Select   
40  Poll Single Select   
41  Poll Single Select   
42  Poll Single Select   
43  Poll Single Select   
44  Poll Single Select   
45  Ask Opinion          
46  Ask Opinion          
47  Ask Opinion          
48  Ask Opinion          
49  Ask Opinion          
50  Ask Opinion          
51  Ask Opinion          
52  Ask Opinion          
53  Ask Opinion          
54  Ask Opinion          
55  Poll Single Select   
56  Ask Opinion          
57  Poll Single Select   
58  Ask Opinion          
59  Poll Single Select   
60  Ask Opinion          
61  Poll Single Select   
62  Ask Opinion          
63  Poll Single Select   
64  Poll Single Select   
65  Ask Experience       

                                                                                                                                                                                question text  
0   Please select your preferred language:                                                                                                                                                     
1   How old are you?                                                                                                                                                                           
2   What is your gender?                                                                                                                                                                       
3   What best describes where you live?                                                                                                                                                        
4   Overall, would you say the increased use of artificial intelligence (AI) in daily life makes you feel…                                                                                     
5   What religious group or faith do you most identify with?                                                                                                                                   
6   What country or region do you most identify with?                                                                                                                                          
7   Thinking about the last three months, how often, if at all, have you noticed AI systems in your daily life?                                                                                
8   Thinking about the last three months, how often, if at all, have you noticed human interactions which have been replaced with automated systems?                                           
9   Thinking about the last three months, how often, if at all, have you been expected to use an AI system at work?                                                                            
10  Thinking about the last three months, how often, if at all, have you personally chosen to use an AI system at work?                                   

## Convergence Analysis

#### Identify Segments and Prepare Data
First, we need a reliable way to get the names of all segment columns used for agreement percentages. We can inspect the columns of the first 'Ask Opinion' DataFrame. We also need to filter qs to only include 'Ask Opinion' questions.

In [45]:
# Import necessary libraries (if not already imported)
import pandas as pd
import numpy as np
from scipy.stats import variation # Keep this if using CV later

# Assuming 'qs' is the list of DataFrames loaded previously (e.g., from JSON)

# --- Direct Filtering of qs ---
# Filter qs directly for 'Ask Opinion' questions
# This checks the 'Question Type' column within each DataFrame
qs_opinion = [
    df for df in qs
    if 'Question Type' in df.columns and not df.empty and df['Question Type'].iloc[0] == 'Ask Opinion'
]

# --- Identify Segment Columns ---
# (This part remains similar, using the first identified 'Ask Opinion' DF)
if qs_opinion:
    first_opinion_df = qs_opinion[0]
    # Determine segment columns - **Double-check the starting index based on your JSON structure**
    # If loaded from the same source CSV logic, index 6 should be correct.
    # Inspect first_opinion_df.columns if unsure.
    segment_start_index = 6
    segment_end_offset = -3 # Exclude last 3 columns (Submitted By, Language, etc.)
    segment_cols = first_opinion_df.columns[segment_start_index:segment_end_offset].tolist()

    print(f"Identified {len(segment_cols)} segment columns from the first 'Ask Opinion' DataFrame.")
    # print(segment_cols) # Optionally print all segment names

    # Define a helper function for safe numeric conversion (can be defined elsewhere too)
    def safe_to_numeric(series):
        return pd.to_numeric(series, errors='coerce')

    # --- Pre-process Filtered DataFrames ---
    qs_opinion_processed = []
    # Now iterate through the correctly filtered qs_opinion list
    for df in qs_opinion:
        df_copy = df.copy()
        for col in segment_cols:
            if col in df_copy.columns:
                df_copy[col] = safe_to_numeric(df_copy[col])
            else:
                df_copy[col] = np.nan # Handle potentially missing segment columns
        qs_opinion_processed.append(df_copy)

    print(f"\\nSuccessfully processed {len(qs_opinion_processed)} 'Ask Opinion' questions for numeric analysis.")

else:
    print("No 'Ask Opinion' questions found in the 'qs' list based on internal 'Question Type'.")
    segment_cols = []
    qs_opinion_processed = []

# --- Retrieve Question Text ---
# If you need the question text later, you can get it from the DataFrame directly
# Example: Get text for the first processed opinion question
if qs_opinion_processed:
    first_question_text = qs_opinion_processed[0]['Question'].iloc[0]
    print(f"\\nExample: Text of first opinion question: '{first_question_text[:100]}...'") # Print first 100 chars
else:
     print("\\nNo processed opinion questions to retrieve text from.")


Identified 259 segment columns from the first 'Ask Opinion' DataFrame.
\nSuccessfully processed 15 'Ask Opinion' questions for numeric analysis.
\nExample: Text of first opinion question: 'Can you explain why you gave that trust score to your AI chatbot?...'


In [46]:
qs_opinion[0]

Question ID Question Type  \
0    9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
1    9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
2    9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
3    9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
4    9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
5    9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
6    9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
7    9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
8    9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
9    9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
10   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
11   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
12   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
13   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
14   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
15   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
16   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
17   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
18   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
19   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
20   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
21   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
22   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
23   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
24   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
25   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
26   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
27   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
28   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
29   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
30   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
31   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
32   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
33   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
34   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
35   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
36   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
37   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
38   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
39   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
40   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
41   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
42   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
43   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
44   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
45   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
46   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
47   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
48   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
49   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
50   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
51   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
52   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
53   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
54   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
55   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
56   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
57   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
58   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
59   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
60   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
61   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
62   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
63   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
64   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
65   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
66   9cc4f2fc-dee9-4196-b1c7-b437544668c8  Ask Opinion    
67   9cc4f2fc-dee9

In [34]:
    # --- DEBUG CELL for Step 1 ---
    question_types_in_processed_list = []
    if qs_opinion_processed:
        for df in qs_opinion_processed:
            # Accessing the question type from the DataFrame itself for verification
            # This assumes the structure [Question ID, Question Type, Question, ...] is consistent
            if 'Question Type' in df.columns and len(df) > 0:
                 # Use iloc[0] assuming type is consistent for all rows in the df
                question_types_in_processed_list.append(df['Question Type'].iloc[0])
            else:
                question_types_in_processed_list.append("Unknown Structure or Empty DF")
        print("\\nQuestion Types found in qs_opinion_processed:")
        print(pd.Series(question_types_in_processed_list).value_counts())
    else:
        print("\\nqs_opinion_processed is empty.")
    # --- END DEBUG CELL ---

\nQuestion Types found in qs_opinion_processed:
Ask Opinion           9
Poll Single Select    6
Name: count, dtype: int64


In [29]:
# --- Response Convergence ---
# Calculate convergence for each response across all segments

response_convergence_data = []

if qs_opinion_processed:
    for i, df in enumerate(qs_opinion_processed):
        question_text = qmeta_opinion.iloc[i]['question text']
        question_id = df['Question ID'].iloc[0] # Assuming Question ID is constant per df

        # Select only the segment columns that actually exist in this df and are numeric
        valid_segment_cols = [col for col in segment_cols if col in df.columns and pd.api.types.is_numeric_dtype(df[col])]

        if not valid_segment_cols:
            continue # Skip if no valid segment columns

        # Calculate Standard Deviation across valid segments for each response
        # Use axis=1 to calculate row-wise
        df['agreement_sd'] = df[valid_segment_cols].std(axis=1, skipna=True)
        df['agreement_mean'] = df[valid_segment_cols].mean(axis=1, skipna=True)
        # Coefficient of Variation (SD/mean), handles scale differences
        # Add small epsilon to mean to avoid division by zero
        df['agreement_cv'] = df['agreement_sd'] / (df['agreement_mean'] + 1e-9)


        for index, row in df.iterrows():
            response_convergence_data.append({
                'Question ID': question_id,
                'Question': question_text,
                'Response': row['English Responses'], # Or 'Original Responses'
                'Mean Agreement': row['agreement_mean'],
                'SD Agreement': row['agreement_sd'],
                'CV Agreement': row['agreement_cv'],
                'Response Index (within Q)': index # Keep track of original row
            })

    # Create a DataFrame for easier sorting and viewing
    response_convergence_df = pd.DataFrame(response_convergence_data)

    # Sort by Standard Deviation (ascending) to find most convergent responses
    most_convergent_responses = response_convergence_df.sort_values(by='SD Agreement', ascending=True).reset_index(drop=True)

    # Sort by Coefficient of Variation (ascending) - alternative convergence measure
    most_convergent_responses_cv = response_convergence_df.sort_values(by='CV Agreement', ascending=True).reset_index(drop=True)


    print("\\n--- Most Convergent Responses (Lowest SD across all segments) ---")
    print(most_convergent_responses[['Question', 'Response', 'Mean Agreement', 'SD Agreement']].head(10)) # Show top 10

    print("\\n--- Most Convergent Responses (Lowest CV across all segments) ---")
    print(most_convergent_responses_cv[['Question', 'Response', 'Mean Agreement', 'SD Agreement', 'CV Agreement']].head(10)) # Show top 10

else:
    print("Cannot calculate response convergence: No processed 'Ask Opinion' data available.")


KeyError: 'English Responses'

In [5]:
show_questions(qs)

question type  \
0   Poll Single Select   
1   Poll Single Select   
2   Poll Single Select   
3   Poll Single Select   
4   Poll Single Select   
..                 ...   
61  Poll Single Select   
62  Ask Opinion          
63  Poll Single Select   
64  Poll Single Select   
65  Ask Experience       

                                                                                                                                                                                question text  
0   Please select your preferred language:                                                                                                                                                     
1   How old are you?                                                                                                                                                                           
2   What is your gender?                                                                                                                                                                       
3   What best describes where you live?                                                                                                                                                        
4   Overall, would you say the increased use of artificial intelligence (AI) in daily life makes you feel…                                                                                     
..                                                                                                     ...                                                                                     
61  Do you agree or disagree?                                                                                                                                                                  
62  Please explain whether you agree or disagree and why.                                                                                                                                      
63  Do you feel you were able to fully express your views on your culture, your values, and what you want for the future in this conversation? (through what you responded and how you voted)  
64  Do you feel like you understand yourself better after participating in this conversation?                                                                                                  
65  Lastly, is there anything you felt you could not express in this conversation that you want to make sure the people working on this know?                                                  

[66 rows x 2 columns]

In [ ]:
segments_df = show_segments(qs)

In [3]:
# prompt: segments_df is a dataframe with Index (starting at 0) and "Segment" column where each value is text formatted like this:
# All(986)
# O1: French (14)
# O1: Chinese (China) (91)
# O1: Hindi (5)
# O1: Portuguese (Portugal) (25)
# O1: English (742)
# O1: Russian (27)
# O1: Spanish (64)
# O1: Arabic (18)
# O2: &lt;18 (0)
# O2: 18-25 (288)
# O2: 26-35 (400)
# etc
# extract the integer within (...) in the text of the Segment. create a dict, key is the integer Index value, value is a dict {"segment": <segment_text>, "count": <integer_count_from_parenthesis>}
# Ensure that the integer extraction from the (..) can also handle these kinds of cases:
# O1: Chinese (China) (91)
# O1: Portuguese (Portugal) (25)

import re

def extract_segment_data(segments_df):
    segment_data = {}
    for index, row in segments_df.iterrows():
        # Access the segment text using the column name returned by show_segments
        # show_segments returns a DataFrame with a single column named 0.
        segment_text = row[0]  # Updated column name
        match = re.search(r'\((\d+)\)', segment_text)
        if match:
            count = int(match.group(1))
            segment_data[index] = {"segment": segment_text, "count": count}
        else:
            # Handle cases where no integer is found within parentheses
            segment_data[index] = {"segment": segment_text, "count": None}
    return segment_data

# Example usage (assuming segments_df is defined)
# Assuming segments_df is already created as shown in the prompt
# Replace with your actual segments_df
# Example segments_df (replace this with your actual data)
#data = {'Segment': ['All(986)', 'O1: French (14)', 'O1: Chinese (China) (91)', 'O1: Hindi (5)', 'O1: Portuguese (Portugal) (25)']}
segments_df = show_segments(qs)

segment_info = extract_segment_data(segments_df)
segment_info


{0: {'segment': 'All(986)', 'count': 986},
 1: {'segment': 'O1: French (14)', 'count': 14},
 2: {'segment': 'O1: Chinese (China) (91)', 'count': 91},
 3: {'segment': 'O1: Hindi (5)', 'count': 5},
 4: {'segment': 'O1: Portuguese (Portugal) (25)', 'count': 25},
 5: {'segment': 'O1: English (742)', 'count': 742},
 6: {'segment': 'O1: Russian (27)', 'count': 27},
 7: {'segment': 'O1: Spanish (64)', 'count': 64},
 8: {'segment': 'O1: Arabic (18)', 'count': 18},
 9: {'segment': 'O2: &lt;18 (0)', 'count': 0},
 10: {'segment': 'O2: 18-25 (288)', 'count': 288},
 11: {'segment': 'O2: 26-35 (400)', 'count': 400},
 12: {'segment': 'O2: 36-45 (184)', 'count': 184},
 13: {'segment': 'O2: 46-55 (85)', 'count': 85},
 14: {'segment': 'O2: 56-65 (21)', 'count': 21},
 15: {'segment': 'O2: 65+ (8)', 'count': 8},
 16: {'segment': 'O3: Male (488)', 'count': 488},
 17: {'segment': 'O3: Female (483)', 'count': 483},
 18: {'segment': 'O3: Non-binary (8)', 'count': 8},
 19: {'segment': 'O3: Other / prefer not t

In [4]:
def filter_segments_by_count(segment_info, min_count):
  filtered_segments = {}
  for segment_id, info in segment_info.items():
    if info["count"] is not None and info["count"] >= min_count:
      filtered_segments[segment_id] = info
  return filtered_segments


In [5]:
# set minimum segment size threshold for considering divergence
MIN_SEG_SIZE = 30 # minimum participants in segment for us to consider checking it in our divergence search

# filter segments to use by threshold
filtered_segments = filter_segments_by_count(segment_info, MIN_SEG_SIZE)

# show count of segments that will be analyzed
print(f"Number of segments to analyze: {len(filtered_segments)}")



Number of segments to analyze: 44


In [19]:
qid = 33
#segs = list(filtered_segments.keys())
segs = [223,224,225,226,227,228]
ba = get_divergent_responses(qs[qid],segs,15)

<ipython-input-2-28fc1b58389c>:149: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dfplt["bridge"] = df.apply (lambda row: min_bridge(row,segs_incl[1:],df.columns), axis=1)
<ipython-input-2-28fc1b58389c>:150: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dfplt["polarization"] = df.apply (lambda row: polarization(row,segs_incl[1:],df.columns), axis=1)
<ipython-input-2-28fc1b58389c>:151: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_i

In [21]:
ba.style.pipe(make_pretty)

In [20]:
ba[['English Responses','divergence']]

English Responses  \
303  Till now I haven't read any article about how AI is using my data. Of course, they are using my data. I am sharing everything with them, but still, I am not sure about the consequences. Till now I trust AI; that's why I asked personal questions as well. If I didn't trust AI, then I wouldn't ask personal questions at all. AI knows all about my family, my occupation, etc. It's scary, but still I am using it. I feel it is a necessity.    
150  Sometimes Chatgpt will hallucinate, which may be a technical limitation. Therefore he may give wrong answers, which is not in my best interest. Supervision and suspicion are needed.                                                                                                                                                                                                                                                                  
288  The reason for giving this trust score to the AI ​​chatbot is that even though it has deep knowledge on most of the topics, it also makes errors and I have experienced this on many occasions. Instead of blindly trusting the information given by it, one must check it at his level once.                                                                                                                                                          
46   In my opinion, AI Chatbot is unbiased in most of its responses. Therefore, the trust score automatically gets high when the results are not varied in accordance to personal values and thoughts.                                                                                                                                                                                                                                                      
805  The Chat GPT quotes "Chat gpt can make mistakes" meaning that it cannot be trusted 100%  so there is some improvements that need to be done for it to be trusted wholly.                                                                                                                                                                                                                                                                               
69   Because AI chat bots are helping us on a daily basis. It makes life easier and I trust they will do the best sometimes. Privacy is a concern. So that's the main reason for low ratings.                                                                                                                                                                                                                                                               
49   I assigned that trust score based on my experiences with AI chatbot's performance dependability, and transparency. While they are often useful for providing quick solutions and assisting with everyday chores, their limits become apparent when dealing with difficult questions. Furthermore, issues such as data privacy, information veracity, and feedback response are big impact on my trust level.                                           
960  Because it is literally impossible for me to have ALL the variables necessary to act in my best interest.                                                                                                                                                                                                                                                                                                                                              
594  I have used chatgpt to prep for some recent interviews. It enabled me to research the most important topics. When I attended the interviews, I felt like I was reasonable prepared because they went well.                                                                                                                                                                                                                    

In [9]:

# pick "Ask Opinion" question ID
qid = 33

# iterate through each possible pair of filtered_segments to calculate divergence via segs = [seg_id1, seg_id2]; ba = get_divergent_responses(qs[qid],segs,3)
# get the ba['divergence'][0] result (the highest divergence value) and save it in a dict of key: set(seg_id1, seg_id2), value: <divergence float>

# segs = ....

In [10]:
#choose question and segments
qid = 33



segs = segs = [231,232,233,234,235,236,0]

#print the question
print(qs[qid]["Question"][1])

#generate a table with bridging, divergence, and consensus metrics; keeping the 3 responses with the hightest divergence
ba = get_divergent_responses(qs[qid],segs,3)

#display a pretty version fo the table
ba.style.pipe(make_pretty)

Can you explain why you gave that trust score to your AI chatbot?


<ipython-input-2-28fc1b58389c>:149: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dfplt["bridge"] = df.apply (lambda row: min_bridge(row,segs_incl[1:],df.columns), axis=1)
<ipython-input-2-28fc1b58389c>:150: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dfplt["polarization"] = df.apply (lambda row: polarization(row,segs_incl[1:],df.columns), axis=1)
<ipython-input-2-28fc1b58389c>:151: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_i

In [22]:
ba['divergence']

608    0.304138
894    0.304138
772    0.304138
777    0.304138
854    0.304138
Name: divergence, dtype: float64